### Read in data

In [1]:
import psycopg2
import pandas as pd
import numpy as np
import time
from datetime import timedelta, datetime
from matplotlib import pyplot as plt
from collections import defaultdict
import random
import pickle

In [5]:
con = psycopg2.connect(user = "postgres",
                       password = "",
                       host = "127.0.0.1",
                       port = "5432",
                       database = "adj_noun_pairs")

try:
    cursor = con.cursor();
except (Exception, psycopg2.Error) as error:
    print("Error in Connection",error)

In [6]:
cursor.execute("SELECT * FROM final_pairs WHERE noun IN (SELECT noun FROM final_pairs GROUP BY noun HAVING COUNT(*) > 2)")
all_pairs = cursor.fetchall()

In [7]:
dup_nouns = [pair[1] for pair in all_pairs]
# Easy naive for-loop to keep order so results wouldn't change each time
nouns = []
for noun in dup_nouns:
    if noun not in nouns:
        nouns.append(noun)

In [8]:
dup_adjectives = [pair[0] for pair in all_pairs]
adjectives = []
for adj in dup_adjectives:
    if adj not in adjectives:
        adjectives.append(adj)

In [9]:
data = pd.DataFrame(0, index=nouns, columns=adjectives)
data.head()

eelmine  järgmine  viimane  käesolev  kogu  kohalik  suur  pikk  \
aasta              0         0        0         0     0        0     0     0   
aeg                0         0        0         0     0        0     0     0   
määrus             0         0        0         0     0        0     0     0   
omavalitsus        0         0        0         0     0        0     0     0   
osa                0         0        0         0     0        0     0     0   

             juriidiline  tulev  ...  realiseeritav  valgustatav  vajuv  \
aasta                  0      0  ...              0            0      0   
aeg                    0      0  ...              0            0      0   
määrus                 0      0  ...              0            0      0   
omavalitsus            0      0  ...              0            0      0   
osa                    0      0  ...              0            0      0   

             väikesekasvuline  väikeseformaadiline  õlirikas  õigusetu  \
aasta                       0                    0         0         0   
aeg                         0                    0         0         0   
määrus                      0                    0         0         0   
omavalitsus                 0                    0         0         0   
osa                         0                    0         0         0   

             oletuslik  raugematu  raudteeäärne  
aasta                0          0             0  
aeg                  0          0             0  
määrus               0          0             0  
omavalitsus          0          0             0  
osa                  0          0             0  

[5 rows x 7358 columns]

In [10]:
for tup in all_pairs:
    data.loc[tup[1], tup[0]] = tup[2]

In [11]:
data.head()

eelmine  järgmine  viimane  käesolev   kogu  kohalik   suur  \
aasta          53250     38107    24410     11753   1115       40    114   
aeg               75        65    27915      1227  24997     1373    194   
määrus            16       110       17     27514     30        0      0   
omavalitsus       30        67       44         0     31    24261     84   
osa              201       436      918       118     51       10  22165   

              pikk  juriidiline  tulev  ...  realiseeritav  valgustatav  \
aasta         1562            0  12634  ...              0            0   
aeg          14913            0     18  ...              0            0   
määrus           0            0      0  ...              0            0   
omavalitsus      0           12      0  ...              0            0   
osa             25            0     17  ...              0            0   

             vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  õigusetu  \
aasta            0                 0                    0         0         0   
aeg              0                 0                    0         0         0   
määrus           0                 0                    0         0         0   
omavalitsus      0                 0                    0         0         0   
osa              0                 0                    0         0         0   

             oletuslik  raugematu  raudteeäärne  
aasta                0          0             0  
aeg                  0          0             0  
määrus               0          0             0  
omavalitsus          0          0             0  
osa                  0          0             0  

[5 rows x 7358 columns]

In [12]:
data.shape

(5817, 7358)

### Non-negative matrix factorization

In [2]:
from sklearn.decomposition import NMF, LatentDirichletAllocation

In [11]:
nmf = NMF(n_components=1000, random_state=0)

In [ ]:
nmf.fit(data)

In [ ]:
results = nmf.transform(data)

In [ ]:
# with open("nmf_model_1000.pickle", "wb") as f:
#     pickle.dump(nmf, f)
# 
# np.save("nmf_model_1000_results_fewer.npy", results)

In [3]:
with open("nmf_model_1000_fewer.pickle", "rb") as f:
    nmf = pickle.load(f)

C:\Users\Birgit\Anaconda3\envs\py36_estnltk\lib\site-packages\sklearn\base.py:334: UserWarning: Trying to unpickle estimator NMF from version 0.22.2.post1 when using version 0.23.2. This might lead to breaking code or invalid results. Use at your own risk.
  UserWarning)


In [14]:
results = np.load("nmf_model_1000_results_fewer.npy")

In [103]:
nmf

NMF(n_components=1000, random_state=0)

In [15]:
print(results.shape, nmf.components_.shape)

(5817, 1000) (1000, 7358)


### Results

In [83]:
adjs_in_topics = pd.DataFrame(nmf.components_, columns=data.columns)

In [84]:
adjs_in_topics.head()

eelmine    järgmine     viimane    käesolev        kogu     kohalik  \
0  208.376391  148.611746   93.410659   17.531211    1.936664    0.000423   
1    0.011375    0.000000  130.988471    1.746031  116.560595    5.927474   
2    0.000000    0.000000    0.000000  219.777499    0.000000    0.000000   
3    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
4    0.000000    0.000000    0.000000    0.000000    0.000000  159.584037   

         suur       pikk  juriidiline      tulev  ...  realiseeritav  \
0    0.006450   1.297714     0.000000  36.987329  ...            0.0   
1    0.277297  69.678960     0.000000   0.000457  ...            0.0   
2    0.000000   0.000000     0.000000   0.000000  ...            0.0   
3  168.105548   0.000000     0.000000   0.000000  ...            0.0   
4    0.000000   0.000000     0.003084   0.000000  ...            0.0   

   valgustatav  vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  \
0          0.0    0.0               0.0                  0.0       0.0   
1          0.0    0.0               0.0                  0.0       0.0   
2          0.0    0.0               0.0                  0.0       0.0   
3          0.0    0.0               0.0                  0.0       0.0   
4          0.0    0.0               0.0                  0.0       0.0   

   õigusetu  oletuslik  raugematu  raudteeäärne  
0       0.0        0.0        0.0           0.0  
1       0.0        0.0        0.0           0.0  
2       0.0        0.0        0.0           0.0  
3       0.0        0.0        0.0           0.0  
4       0.0        0.0        0.0           0.0  

[5 rows x 7358 columns]

In [85]:
nouns_in_topics = pd.DataFrame(results, index=data.index)

In [86]:
nouns_in_topics.head()

0           1           2           3           4    \
aasta        253.056032    0.000000   18.949543    0.520472    0.231719   
aeg            0.002546  208.138755    3.789025    0.659335    0.869002   
määrus         0.000000    0.000000  118.611396    0.000000    0.000000   
omavalitsus    0.000000    0.000000    0.000000    0.354618  152.024585   
osa            0.000000    0.000702    0.073491  131.135476    0.033043   

                  5    6          7    8         9    ...  990       991  992  \
aasta        2.733681  0.0  21.990411  0.0  4.171233  ...  0.0  0.000000  0.0   
aeg          1.208701  0.0   3.389497  0.0  6.158924  ...  0.0  0.003702  0.0   
määrus       0.125033  0.0   0.459119  0.0  0.250419  ...  0.0  0.000000  0.0   
omavalitsus  0.000000  0.0   0.655777  0.0  0.236073  ...  0.0  0.000000  0.0   
osa          0.041860  0.0   0.000000  0.0  0.007498  ...  0.0  0.000071  0.0   

             993  994       995  996       997  998  999  
aasta        0.0  0.0  0.209587  0.0  0.043943  0.0  0.0  
aeg          0.0  0.0  0.000000  0.0  0.000000  0.0  0.0  
määrus       0.0  0.0  0.000000  0.0  0.000000  0.0  0.0  
omavalitsus  0.0  0.0  0.000000  0.0  0.000000  0.0  0.0  
osa          0.0  0.0  0.027342  0.0  0.000000  0.0  0.0  

[5 rows x 1000 columns]

In [24]:
sort = adjs_in_topics.loc[2].sort_values(ascending=False)
sort[sort * 100 > sort[0]]

käesolev     219.777499
kõnealune      2.604750
käsitlev       2.335547
Name: 2, dtype: float64

In [25]:
informative_adjs = {}

for i in range(1000):
    sort = adjs_in_topics.loc[i].sort_values(ascending=False)
    informative_adjs[i] = sort[sort * 100 > sort[0]]

In [27]:
nouns_in_topics.loc['aasta'].idxmax()

0

In [28]:
from collections import defaultdict

In [87]:
topics = defaultdict(list)

for i, row in nouns_in_topics.iterrows():
    topics[row.idxmax()].append(i)

In [221]:
import pickle

with open("nmf_topics.pickle", "wb") as f:
    pickle.dump(topics, f)

In [88]:
print(topics[2])

['määrus', 'seadus', 'direktiiv', 'paragrahv', 'leping', 'artikkel', 'konventsioon', 'lisa', 'protokoll', 'seadustik', 'peatükk', 'loend', 'koodeks']


In [103]:
long_topics = []
short_topics = []
empty_topics = []
one_word_topics = []
medium_topics = []

for i in range(1000):
    topic_len = len(topics[i])
    if topic_len >= 100:
        long_topics.append(i)
    elif topic_len <= 5 and topic_len > 1:
        short_topics.append(i)
    elif topic_len == 1:
        one_word_topics.append(i)
    elif topic_len == 0:
        empty_topics.append(i)
    else:
        medium_topics.append(i)

In [104]:
print(f"{len(long_topics)} topics have 100 words or more")
print(f"{len(short_topics)} topics have between 2 and 5 words")
print(f"{len(one_word_topics)} topics have 1 word")
print(f"{len(empty_topics)} topics have 0 words")
print(f"{len(medium_topics)} topic lengths are between 5 and 100 (not included)")

10 topics have 100 words or more
155 topics have between 2 and 5 words
197 topics have 1 word
456 topics have 0 words
182 topic lengths are between 5 and 100 (not included)


In [105]:
for i in long_topics:
    print(i, len(topics[i]))

3 109
7 186
85 131
213 154
244 129
424 166
501 118
524 158
556 151
622 163


#### Random topics

In [136]:
for i in range(1000):
    if 'mees' in topics[i]:
        print(i, topics[i])

11 ['inimene', 'mees']


In [138]:
adjs_in_topics.loc[11].sort_values(ascending=False).head(10)

noor      95.054552
olnud     24.684741
elav      21.774707
vana      20.887732
uus       18.958860
tark      17.596490
võõras    13.610910
olev      13.111816
tulnud    11.404473
töötav     9.697630
Name: 11, dtype: float64

258, 82, 981, 390, 490

In [174]:
print(topics[981])

['õhtutund', 'öötund', 'ärkaja']


In [168]:
rand = random.randint(0, 999)
print(rand, topics[rand] if len(topics[rand]) < 100 else len(topics[rand]))

490 ['kontroll', 'dieet', 'järgimine', 'julgeolekumeede', 'kvaliteedinõue', 'turvanõue']


#### Kuud

In [37]:
kuud = ['jaanuar', 'veebruar', 'märts', 'aprill', 'mai', 'juuni', 'juuli', 'august', 'september', 'oktoober', 'november', 'detsember']
idx = []

for kuu in kuud:
    for topic, words in topics.items():
        if kuu in words:
            idx.append(topic)
            continue

In [38]:
idx

[237, 237, 244, 244, 237, 631, 141, 141, 141, 141, 141]

In [42]:
for i in set(idx):
    print(f"topic {i}, with {idx.count(i)} month(s), length {len(topics[i])}")
    print(topics[i])
    print("Most common adjectives in topic:")
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

topic 244, with 2 month(s), length 129
['õnn', 'saade', 'kontakt', 'suu', 'lahendamine', 'lapsepõli', 'kasutus', 'haige', 'kokkupuude', 'avalikkus', 'õnnestumine', 'modell', 'vastavus', 'nooruk', 'kokkupõrge', 'inspektor', 'haigekassa', 'agent', 'pistmine', 'pretensioon', 'erastamine', 'abielupaar', 'alkoholijoove', 'häbi', 'kiir', 'vahendaja', 'solvang', 'kiusatus', 'arutlus', 'kalduvus', 'eluaeg', 'rahvaliit', 'riigivara', 'aastasada', 'kapten', 'tuletõrjuja', 'rool', 'eestvedaja', 'serblane', 'diplomaat', 'sünnipäev', 'kopter', 'reformierakond', 'püstol', 'annetaja', 'riigikontroll', 'kaitseliitlane', 'turvamees', 'möödalaskmine', 'helistaja', 'kaklus', 'lahkarvamus', 'maavalitsus', 'reisirong', 'rahandusministeerium', 'müüja', 'siseministeerium', 'okupatsioon', 'töökord', 'kurd', 'julgus', 'era', 'ida', 'selts', 'leke', 'tolk', 'välisministeerium', 'lätlane', 'kanep', 'isamaaliit', 'kujundamine', 'taotleja', 'juhtunu', 'ühispank', 'rahanduskomisjon', 'sõlmimine', 'kaitseministeeriu

#### Päevad

In [43]:
days = ['esmaspäev', 'teisipäev', 'kolmapäev', 'neljapäev', 'reede', 'laupäev', 'pühapäev']
idx2 = []

for day in days:
    for topic, words in topics.items():
        if day in words:
            idx2.append(topic)
            continue

In [44]:
idx2

[420, 30, 30, 30, 141, 141, 141]

In [45]:
for i in set(idx2):
    print(i, ":", topics[i])
    print("Most common adjectives in topic:")
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

420 : ['kevad', 'esmaspäev', 'kiirgus', 'reostus']
Most common adjectives in topic:
tulev      9.751185
saabuv     0.539388
eelolev    0.505333
jahe       0.161760
lähenev    0.128286
Name: 420, dtype: float64
----------------------------
141 : ['reede', 'nädalavahetus', 'laupäev', 'pühapäev', 'rong', 'nädalalõpp', 'pankrot', 'trumm', 'kuul', 'detsember', 'kuulujutt', 'oktoober', 'september', 'tera', 'november', 'välismaa', 'august', 'liig']
Most common adjectives in topic:
läinud     13.402027
karjuv      0.102369
kihutav     0.091521
lähenev     0.067414
suunduv     0.062449
Name: 141, dtype: float64
----------------------------
30 : ['nädal', 'kuu', 'valimine', 'hooaeg', 'kord', 'rekord', 'riigikogu', 'mäng', 'suvi', 'sajand', 'kümnend', 'käive', 'peaminister', 'lõige', 'õhtu', 'sügis', 'neljapäev', 'koosseis', 'volikogu', 'tippmark', 'kolmapäev', 'linnapea', 'tali', 'lõik', 'direktor', 'juhtkond', 'kvartal', 'linnavalitsus', 'välisminister', 'teisipäev', 'vabariik', 'siseminister',

In [129]:
len(topics[30])

90

#### Aastaajad

In [110]:
aastaajad = ['talv', 'sügis', 'kevad', 'suvi']
idx7 = []

for a in aastaajad:
    for topic, words in topics.items():
        if a in words:
            idx7.append(topic)
            continue

In [111]:
idx7

[451, 30, 420, 30]

In [112]:
for i in set(idx7):
    print(i, ":", topics[i])
    print("Most common adjectives in topic:")
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

451 : ['pinnas', 'talv', 'nisu', 'mööbel', 'maandumine', 'üleminek', 'iste', 'kude', 'kaas', 'lapp', 'muld', 'voodi', 'mänguasi', 'põld', 'kumm', 'vedrustus', 'köide', 'talveilm', 'padi', 'tugitool', 'diivan', 'tald', 'helkur', 'loomake', 'hari', 'maapind', 'või', 'tämber', 'teivas', 'suss', 'ase']
Most common adjectives in topic:
pehme      7.251118
mugav      0.354862
harilik    0.298386
söödav     0.269540
õhuke      0.162153
Name: 451, dtype: float64
----------------------------
420 : ['kevad', 'esmaspäev', 'kiirgus', 'reostus']
Most common adjectives in topic:
tulev      9.751185
saabuv     0.539388
eelolev    0.505333
jahe       0.161760
lähenev    0.128286
Name: 420, dtype: float64
----------------------------
30 : ['nädal', 'kuu', 'valimine', 'hooaeg', 'kord', 'rekord', 'riigikogu', 'mäng', 'suvi', 'sajand', 'kümnend', 'käive', 'peaminister', 'lõige', 'õhtu', 'sügis', 'neljapäev', 'koosseis', 'volikogu', 'tippmark', 'kolmapäev', 'linnapea', 'tali', 'lõik', 'direktor', 'juhtkond

#### Elukutsed

In [114]:
jobs = ['laulja', 'näitleja', 'kunstnik', 'tantsija', 'artist']
idx3 = []

for job in jobs:
    for topic, words in topics.items():
        if job in words:
            idx3.append(topic)
            continue

In [115]:
idx3

[501, 501, 501, 422, 354]

In [134]:
for i in set(idx3):
    print(i, ":", topics[i])
    print("Most common adjectives in topic:")
    print(adjs_in_topics.loc[i][adjs_in_topics.loc[i] > 1].sort_values(ascending=False).head())
    print("----------------------------")

354 : ['nõudlus', 'kapital', 'sari', 'toiduaine', 'õlu', 'bänd', 'toodang', 'telekanal', 'köögivili', 'ansambel', 'seriaal', 'õun', 'tooraine', 'tarbimine', 'toidukaup', 'esineja', 'maasikas', 'tomat', 'mari', 'artist', 'vili', 'linateos', 'kadu', 'tootmisharu', 'mesi', 'ostuhuvi', 'sääst', 'toore', 'investeerimisfond', 'teleseriaal', 'jäätis', 'säästmine', 'õlletootja', 'õlleturg', 'põllumajandustootja']
Most common adjectives in topic:
kodumaine    3.704984
Name: 354, dtype: float64
----------------------------
501 : ['naine', 'näitleja', 'kunstnik', 'õpetaja', 'laulja', 'neid', 'spetsialist', 'autor', 'neiu', 'tütarlaps', 'lavastaja', 'talent', 'helilooja', 'disainer', 'organism', 'arhitekt', 'pianist', 'lauljatar', 'töötus', 'dirigent', 'moekunstnik', 'mängumees', 'luuletaja', 'kotkas', 'abiline', 'näitlejanna', 'kukk', 'režissöör', 'peategelane', 'armuke', 'armastaja', 'solist', 'talunik', 'väravavaht', 'jalgrattur', 'poksija', 'rezhissöör', 'õppejõud', 'inglane', 'ujuja', 'tartla

In [133]:
len(topics[501])

118

#### Spordialad

In [117]:
spordialad = ['jalgpall', 'korvpall', 'pesapall', 'võrkpall', 'golf', 'tennis']
idx4 = []

for spordiala in spordialad:
    for topic, words in topics.items():
        if spordiala in words:
            idx4.append(topic)
            continue

In [118]:
idx4

[463, 463, 622]

In [132]:
for i in set(idx4):
    print(i, ":", topics[i])
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

622 : ['saal', 'kiri', 'raamat', 'vein', 'ruum', 'daam', 'laev', 'suhkur', 'pipar', 'leht', 'nahk', 'hobune', 'särk', 'pesu', 'pulber', 'lumi', 'pind', 'sokk', 'viin', 'laik', 'vaip', 'lammas', 'paber', 'roos', 'kuld', 'riie', 'taldrik', 'suits', 'lina', 'kleit', 'muna', 'tiib', 'pluus', 'küünal', 'äär', 'sõstar', 'põhi', 'silt', 'serv', 'rätik', 'telk', 'triip', 'king', 'riis', 'kinnas', 'lind', 'rõivas', 'vares', 'hiinlane', 'šokolaad', 'riietus', 'viinamari', 'rass', 'hammas', 'plekk', 'vöö', 'terror', 'nupp', 'õis', 'vest', 'maal', 'klaver', 'tõug', 'täpp', 'raam', 'kombinatsioon', 'müra', 'jõulud', 'kangas', 'kile', 'alagrupp', 'paberileht', 'lill', 'kepp', 'kärbseseen', 'kardin', 'saabas', 'lauavein', 'niit', 'torn', 'värvus', 'aut', 'riba', 'ihk', 'barett', 'lips', 'tennis', 'limusiin', 'triiksärk', 'rätt', 'kaubik', 'paviljon', 'ruut', 'nahavärv', 'neeger', 'kana', 'rääkimine', 'krae', 'tõu', 'kasukas', 'rüü', 'vill', 'sukk', 'jahu', 'lumevaip', 'vihik', 'luik', 'põll', 'pits',

#### Jaccardi topic

In [47]:
for i, words in topics.items():
    if 'automaatkast' in words:
        print(i, words)

184 ['avamine', 'vastuvõtt', 'õhtusöök', 'tseremoonia', 'lõpetamine', 'puhk', 'jumalateenistus', 'rivistus', 'lõunasöök', 'automaatkäigukast', 'rongkäik', 'tähistamine', 'käsikast', 'paraad', 'automaatkast', 'heiskamine', 'esilinastus', 'allakirjutamine']


### Finding properties of nouns

In [239]:
def top_10_nouns_for_adjective(results, adj_index):
    probs= [(index, result) for index, result in enumerate(results[:, adj_index])]
    sorted_probs = sorted(probs, key=lambda x: x[1], reverse=True)
    top_10 = [x[0] for x in sorted_probs[:10]]
    return data.iloc[top_10]

In [294]:
adjs_in_topics['suur'].sort_values(ascending=False).head(30)

117    8199.802526
413    1336.639297
150    1188.448939
386     868.840008
790     832.988945
391     590.443490
458     516.401867
645     479.115369
91      446.444327
308     408.189959
332     380.885850
334     343.942925
283     305.995243
648     287.046072
319     281.847210
179     280.739976
802     245.591872
614     242.839375
809     241.060748
640     238.188194
348     232.696925
459     228.706676
722     201.458964
254     196.473566
3       168.105548
351     161.566304
93      159.816820
453     156.417401
619     155.716079
672     154.726011
Name: suur, dtype: float64

In [299]:
adjs_in_topics.loc[3].sort_values(ascending=False).head(10)

suur               168.105548
südamlik             0.103061
99protsendiline      0.035807
kaduvväike           0.023983
90protsendiline      0.021445
95protsendiline      0.020887
ülisuur              0.013005
80protsendiline      0.011030
nullilähedane        0.008894
puutetundlik         0.008751
Name: 3, dtype: float64

In [300]:
top_10_nouns_for_adjective(results, 3)[['suur']]

suur
osa        22165
tänu       16634
hulk        7429
tõenäosus   4471
kogus       3050
huvi        3032
summ        2779
probleem    2863
raha        2464
saal        2066

In [242]:
adjs_in_topics['uus'].sort_values(ascending=False).head(10)

150    12195.991148
391     9102.280665
790     2825.844793
601     1532.686290
329     1264.177090
727     1260.919249
355     1210.322228
458     1136.252024
319     1135.815635
250      749.967033
Name: uus, dtype: float64

In [302]:
adjs_in_topics.loc[391].sort_values(ascending=False).head(10)

uus               9102.280665
rahvusvaheline    9043.195120
käesolev          8762.446924
vaheline          8657.255786
vastav            7497.244381
kehtiv            6262.671555
pikaajaline       5403.815152
kirjalik          5254.013281
kahjulik          4621.468205
kaheaastane       4408.103469
Name: 391, dtype: float64

In [303]:
top_10_nouns_for_adjective(results, 391)[['uus']]

uus
leping       1495
harjumus       21
bakter         12
toime           0
organism        0
kõrvalmõju      0
heide           0
ühend          17
mõjutus         0
kõrvaltoime     0

In [244]:
adjs_in_topics['endine'].sort_values(ascending=False).head(10)

150    697.400714
117    593.971157
44     521.828641
691    360.220946
873    301.205502
717    268.224100
913    266.114454
751    223.610518
226    180.175793
722    138.258342
Name: endine, dtype: float64

In [253]:
top_10_nouns_for_adjective(results, 44)[['endine']]

endine
president      1216
peaminister    1289
kommunist       562
nõukogu        1577
kolleeg         472
esimees         532
juhatus         487
abikaasa        461
politseinik     366
töötaja         732

In [252]:
adjs_in_topics.loc[44].sort_values(ascending=False).head(10)

endine           521.828641
kunagine          20.895209
kauaaegne          9.844183
vastne             2.826309
vanameelne         1.088511
elukutseline       0.887018
lisav              0.811860
ideeline           0.690295
tulihingeline      0.634262
domineeriv         0.471452
Name: 44, dtype: float64

In [254]:
adjs_in_topics['valge'].sort_values(ascending=False).head(10)

117    502.624990
348    262.158179
831     88.718048
23      67.672624
751     50.148131
972     49.889762
283     47.532032
834     43.727873
29      37.499017
696     24.112011
Name: valge, dtype: float64

In [265]:
adjs_in_topics.loc[23].sort_values(ascending=False).head(10)

valge              67.672624
asuv               18.956823
vana               18.393150
väike               8.819742
kogu                8.130725
mahajäetud          4.829210
terve               4.452422
põlev               4.311258
tühi                3.913527
viiekorruseline     3.248871
Name: 23, dtype: float64

In [266]:
top_10_nouns_for_adjective(results, 23)[['valge']]

valge
maja         4218
laev          307
hoone          20
mees          598
värv          441
suhkur        580
leht          195
vein          901
paneelmaja      0
talu            0

In [304]:
adjs_in_topics['märg'].sort_values(ascending=False).head(10)

229    88.751685
983    55.416332
831    42.972739
648    39.715497
466    17.531067
848    16.966281
158    14.311562
103    14.209879
830    13.947770
842    13.492545
Name: märg, dtype: float64

In [305]:
adjs_in_topics.loc[229].sort_values(ascending=False).head(10)

märg          88.751685
linane        34.471871
niiske        24.263576
puuvillane    21.800562
liibuv        14.528409
kuiv          12.973862
õhuke          7.810520
hele           7.579830
sile           7.493033
ruuduline      7.382375
Name: 229, dtype: float64

In [306]:
top_10_nouns_for_adjective(results, 229)[['märg']]

märg
riie       89
asfalt    103
haud       90
lumi       64
lapp       45
särk       26
T-särk     39
liiv       37
muld       19
unenägu    38

In [307]:
adjs_in_topics['kuiv'].sort_values(ascending=False).head(10)

648    336.267671
353    287.203241
895    139.403766
283    126.180414
831     55.246047
848     52.268355
158     47.564077
727     40.311248
614     28.606318
19      28.049541
Name: kuiv, dtype: float64

In [312]:
adjs_in_topics.loc[895].sort_values(ascending=False).head(10)

kuiv       139.403766
tundlik     73.100877
rasune      52.221545
hele        30.200606
ehtne       24.360959
vananev     21.288727
sile        19.563701
pruun       14.923449
tõmmu       13.525489
paks        13.139681
Name: 895, dtype: float64

In [313]:
top_10_nouns_for_adjective(results, 895)[['kuiv']]

kuiv
nahk         286
trenn         77
köha          50
jalg         115
fakt          41
hein          38
statistika    34
asfalt        35
puu           42
kliima        33

## Informative adjectives per topic

In [48]:
sort = adjs_in_topics.loc[3].sort_values(ascending=False)
sort[sort * 100 > sort[0]]

suur    168.105548
Name: 3, dtype: float64

In [49]:
informative_adjs = {}

for i in range(1000):
    sort = adjs_in_topics.loc[i].sort_values(ascending=False)
    informative_adjs[i] = sort[sort * 100 > sort[0]]

In [50]:
for i in range(1000):
    if len(informative_adjs[i].index) == 1:
        print(i, len(topics[i]) if len(topics[i]) > 50 else topics[i])
        print(informative_adjs[i])
        print()

3 109
suur    168.105548
Name: 3, dtype: float64

4 ['omavalitsus', 'omavalitsusüksus', 'konstaabel', 'maksuamet', 'jahimees', 'miilits', 'pensioniamet', 'keskkonnateenistus', 'tööhõiveamet', 'päästeteenistus', 'võimumees', 'prominent', 'politseiprefektuur', 'seltsielu', 'kriminaalpolitsei', 'murre', 'müügimaks', 'eestlaskond', 'koda', 'bussiliiklus']
kohalik    159.584037
Name: 4, dtype: float64

5 ['meel', 'tahe', 'näide', 'tahtmine', 'isu', 'minek', 'läbisaamine', 'suhtleja', 'klapp', 'äriidee', 'huumorimeel', 'näitlejatöö', 'vaist', 'juhitavus', 'meeskonnatöö', 'organisaator', 'sooritus', 'teenimisvõimalus', 'stardipositsioon', 'müügimees', 'jaanipäev', 'intuitsioon', 'sait', 'füüsis', 'valdamine', 'administraator', 'lapsehoidja']
hea    221.608623
Name: 5, dtype: float64

7 186
uus    132.110573
Name: 7, dtype: float64

10 ['suhe', 'arvamus', 'sektor', 'teenistus', 'konkurss', 'haldus', 'vargus', 'müük', 'esinemine', 'teenistuja', 'käimla', 'väljapanek', 'tulek', 'emissioon', 'akt

In [175]:
one_adj = []
for i in range(1000):
    if len(informative_adjs[i].index) == 1:
        one_adj.extend(informative_adjs[i].index)

In [178]:
print(one_adj)

['suur', 'kohalik', 'hea', 'uus', 'avalik', 'keskmine', 'rahvusvaheline', 'isiklik', 'eelmine', 'ühine', 'kõrge', 'riiklik', 'täis', 'tugev', 'must', 'külm', 'kehaline', 'vana', 'vaba', 'viimane', 'viimane', 'erinev', 'vaikne', 'alaline', 'läinud', 'tulumaksuvaba', 'vastav', 'vaba', 'seotud', 'vastutav', 'olnud', 'õrn', 'oma', 'tehniline', 'uus', 'peamine', 'korralik', 'oluline', 'vastastikune', 'negatiivne', 'järgmine', 'tõsine', 'sobiv', 'tänane', 'eelmine', 'täiendav', 'oluline', 'poliitiline', 'positiivne', 'kindel', 'üldine', 'käsitlev', 'praegune', 'olev', 'kuuluv', 'konkreetne', 'võimalik', 'elav', 'põllumajanduslik', 'võrdne']


In [181]:
one_adj_len = []
for i in range(1000):
    if len(informative_adjs[i].index) == 1:
        one_adj_len.append((informative_adjs[i].index[0], len(topics[i])))

In [182]:
print(sorted(one_adj_len, key=lambda x: x[1], reverse=True))

[('uus', 186), ('seotud', 154), ('vana', 131), ('olnud', 129), ('suur', 109), ('eelmine', 90), ('negatiivne', 74), ('erinev', 68), ('järgmine', 57), ('vastav', 49), ('üldine', 45), ('viimane', 44), ('tänane', 40), ('avalik', 34), ('võimalik', 28), ('hea', 27), ('keskmine', 25), ('rahvusvaheline', 23), ('kohalik', 20), ('oluline', 20), ('läinud', 18), ('vastastikune', 18), ('kõrge', 16), ('täiendav', 16), ('tugev', 14), ('poliitiline', 14), ('ühine', 13), ('elav', 12), ('täis', 10), ('vastutav', 8), ('korralik', 8), ('kuuluv', 8), ('sobiv', 7), ('kehaline', 6), ('positiivne', 6), ('must', 5), ('vaba', 5), ('konkreetne', 5), ('riiklik', 4), ('alaline', 4), ('isiklik', 2), ('külm', 2), ('tehniline', 2), ('vaikne', 1), ('oluline', 1), ('viimane', 0), ('tulumaksuvaba', 0), ('vaba', 0), ('õrn', 0), ('oma', 0), ('uus', 0), ('peamine', 0), ('tõsine', 0), ('eelmine', 0), ('kindel', 0), ('käsitlev', 0), ('praegune', 0), ('olev', 0), ('põllumajanduslik', 0), ('võrdne', 0)]


In [183]:
no_dup = []

for adj in one_adj:
    if adj in no_dup:
        print(adj)
    else:
        no_dup.append(adj)

viimane
vaba
uus
eelmine
oluline


In [184]:
for adj_len in one_adj_len:
    if adj_len[0] in ['viimane', 'vaba', 'uus', 'eelmine', 'oluline']:
        print(adj_len)

('uus', 186)
('eelmine', 90)
('vaba', 5)
('viimane', 44)
('viimane', 0)
('vaba', 0)
('uus', 0)
('oluline', 20)
('eelmine', 0)
('oluline', 1)


In [199]:
for i in range(1000):
    if len(informative_adjs[i].index) == 1 and informative_adjs[i].index[0] == 'oluline':
        print(i, len(topics[i]) if len(topics[i]) > 50 else topics[i])
        print(informative_adjs[i])
        print()

367 ['roll', 'muutus', 'panus', 'komponent', 'märksõna', 'kaubanduspartner', 'verstapost', 'piiramine', 'lünk', 'mõjutaja', 'indikaator', 'vältimine', 'sade', 'hinnamuutus', 'tunnusjoon', 'asitõend', 'infoallikas', 'vajakajäämine', 'tegevussuund', 'kärpimine']
oluline    85.316343
Name: 367, dtype: float64

550 ['vähendamine']
oluline    30.986143
Name: 550, dtype: float64



In [186]:
for i in range(1000):
    if len(informative_adjs[i].index) == 1 and informative_adjs[i].index[0] == 'uus':
        print(i, len(topics[i]) if len(topics[i]) > 50 else topics[i])
        print(informative_adjs[i])
        print()

7 186
uus    132.110573
Name: 7, dtype: float64

327 []
uus    126.094125
Name: 327, dtype: float64



In [191]:
adjs_in_topics.loc[327].sort_values(ascending=False).head(10)

uus                 126.094125
lisav                 0.203022
vahune                0.015073
bilansivõimeline      0.014543
sõlmiv                0.013812
keskpikk              0.012709
ränkraske             0.006392
kauane                0.005554
kuuekäiguline         0.003877
tipp-topp             0.002885
Name: 327, dtype: float64

In [193]:
adjs_in_topics.loc[7].sort_values(ascending=False).head(10)

uus                  132.110573
sõjajärgne             0.049902
pealekasvav            0.039013
sirguv                 0.029260
tasuv                  0.011083
kolmekümnene           0.009507
kolmekümneaastane      0.009248
pealetulev             0.008128
jõudev                 0.005147
epileptiline           0.004681
Name: 7, dtype: float64

In [197]:
nouns_in_topics[327].sort_values(ascending=False).head(10)

kord           4.387150
liikmesriik    3.098296
jõud           3.076310
elu            2.926107
rekord         2.584452
suund          2.541326
investor       1.952225
riik           1.936265
nimi           1.775909
mees           1.618230
Name: 327, dtype: float64

In [198]:
for noun in nouns_in_topics[327].sort_values(ascending=False).head(10).index:
    for i in range(1000):
        if noun in topics[i]:
            print(i, noun, topics[i])
            print("-------------------------")

30 kord ['nädal', 'kuu', 'valimine', 'hooaeg', 'kord', 'rekord', 'riigikogu', 'mäng', 'suvi', 'sajand', 'kümnend', 'käive', 'peaminister', 'lõige', 'õhtu', 'sügis', 'neljapäev', 'koosseis', 'volikogu', 'tippmark', 'kolmapäev', 'linnapea', 'tali', 'lõik', 'direktor', 'juhtkond', 'kvartal', 'linnavalitsus', 'välisminister', 'teisipäev', 'vabariik', 'siseminister', 'peadirektor', 'lugemine', 'parlament', 'kaitseminister', 'valitsuskoalitsioon', 'periood', 'majandusaasta', 'abielu', 'põllumajandusminister', 'haridusminister', 'presidendivalimine', 'eelarveaasta', 'juhendaja', 'peasekretär', 'kooliaasta', 'vallavanem', 'parlamendivalimine', 'olümpia', 'kalendriaasta', 'postitus', 'tiitlivõistlus', 'õiguskantsler', 'keskkonnaminister', 'administratsioon', 'netokäive', 'finaalturniir', 'riigikontrolör', 'tsükkel', 'iseseisvusaeg', 'tuur', 'rahvaloendus', 'linnavolikogu', 'play-off', 'oksjon', 'suurvõistlus', 'prefekt', 'MM-võistlus', 'parandusettepanek', 'avatar', 'vallavalitsus', 'valimiskam

In [67]:
yks = 0
for i in range(1000):
    if len(informative_adjs[i].index) == 1:
        yks += 1

In [68]:
yks

60

In [51]:
v2rske = ['liha', 'kurk', 'salat', 'puuvili', 'köögivili', 'viinamari', 'kapsas', 'maasikas', 'mari', 'abielumees', 'seen', 'saiake']
idx3 = []

for asi in v2rske:
    for topic, words in topics.items():
        if asi in words:
            idx3.append(topic)
            continue

In [52]:
idx3

[764, 406, 92, 651, 354, 622, 556, 354, 354, 501, 622, 92]

In [53]:
for i in set(idx3):
    print(i, ":", topics[i])
    print("Most common adjectives in topic:")
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

354 : ['nõudlus', 'kapital', 'sari', 'toiduaine', 'õlu', 'bänd', 'toodang', 'telekanal', 'köögivili', 'ansambel', 'seriaal', 'õun', 'tooraine', 'tarbimine', 'toidukaup', 'esineja', 'maasikas', 'tomat', 'mari', 'artist', 'vili', 'linateos', 'kadu', 'tootmisharu', 'mesi', 'ostuhuvi', 'sääst', 'toore', 'investeerimisfond', 'teleseriaal', 'jäätis', 'säästmine', 'õlletootja', 'õlleturg', 'põllumajandustootja']
Most common adjectives in topic:
kodumaine      3.704984
välismaine     0.996086
eestimaine     0.459805
kvaliteetne    0.378452
omamaine       0.372337
Name: 354, dtype: float64
----------------------------
651 : ['tüüp', 'maine', 'au', 'vend', 'seltskond', 'sõiduk', 'taust', 'päritolu', 'tegelane', 'kott', 'välimus', 'vaikus', 'kraam', 'ümbrik', 'maik', 'puuvili', 'värk', 'pakk', 'kuulsus', 'kilekott', 'kamp', 'tablett', 'kohver', 'finantsinstitutsioon', 'fail', 'sell', 'vedelik', 'pangaarve', 'paljastus', 'saadetis', 'afäär', 'hansapäev', 'säde', 'ilmutus', 'penalti', 'alge', 'inve

#### title

In [54]:
adjs_topics = adjs_in_topics.copy()

In [55]:
nouns_topics = nouns_in_topics.copy()

In [56]:
for i in adjs_topics.index:
    adjs_topics.loc[i][adjs_topics.loc[i] * 10 < adjs_topics.loc[i].max()] = 0

In [57]:
for i in nouns_topics.columns:
    nouns_topics[i][nouns_topics[i] * 10 < nouns_topics[i].max()] = 0

In [58]:
adjs_topics.head()

eelmine    järgmine     viimane    käesolev        kogu     kohalik  \
0  208.376391  148.611746   93.410659    0.000000    0.000000    0.000000   
1    0.000000    0.000000  130.988471    0.000000  116.560595    0.000000   
2    0.000000    0.000000    0.000000  219.777499    0.000000    0.000000   
3    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
4    0.000000    0.000000    0.000000    0.000000    0.000000  159.584037   

         suur      pikk  juriidiline      tulev  ...  realiseeritav  \
0    0.000000   0.00000          0.0  36.987329  ...            0.0   
1    0.000000  69.67896          0.0   0.000000  ...            0.0   
2    0.000000   0.00000          0.0   0.000000  ...            0.0   
3  168.105548   0.00000          0.0   0.000000  ...            0.0   
4    0.000000   0.00000          0.0   0.000000  ...            0.0   

   valgustatav  vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  \
0          0.0    0.0               0.0                  0.0       0.0   
1          0.0    0.0               0.0                  0.0       0.0   
2          0.0    0.0               0.0                  0.0       0.0   
3          0.0    0.0               0.0                  0.0       0.0   
4          0.0    0.0               0.0                  0.0       0.0   

   õigusetu  oletuslik  raugematu  raudteeäärne  
0       0.0        0.0        0.0           0.0  
1       0.0        0.0        0.0           0.0  
2       0.0        0.0        0.0           0.0  
3       0.0        0.0        0.0           0.0  
4       0.0        0.0        0.0           0.0  

[5 rows x 7358 columns]

In [59]:
nouns_topics.head()

0           1           2           3           4    5    \
aasta        253.056032    0.000000   18.949543    0.000000    0.000000  0.0   
aeg            0.000000  208.138755    0.000000    0.000000    0.000000  0.0   
määrus         0.000000    0.000000  118.611396    0.000000    0.000000  0.0   
omavalitsus    0.000000    0.000000    0.000000    0.000000  152.024585  0.0   
osa            0.000000    0.000000    0.000000  131.135476    0.000000  0.0   

             6          7    8    9    ...  990  991  992  993  994       995  \
aasta        0.0  21.990411  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.209587   
aeg          0.0   3.389497  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.000000   
määrus       0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.000000   
omavalitsus  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.000000   
osa          0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.000000   

             996  997  998  999  
aasta        0.0  0.0  0.0  0.0  
aeg          0.0  0.0  0.0  0.0  
määrus       0.0  0.0  0.0  0.0  
omavalitsus  0.0  0.0  0.0  0.0  
osa          0.0  0.0  0.0  0.0  

[5 rows x 1000 columns]

In [60]:
dot_val = np.dot(nouns_topics, adjs_topics)

In [61]:
dot_df = pd.DataFrame(dot_val, index=data.index, columns=data.columns)

In [62]:
dot_df.head()

eelmine      järgmine       viimane      käesolev  \
aasta        52837.135410  37873.298199  24168.776075   7331.224946   
aeg              0.000000      0.000000  27882.051973      0.000000   
määrus          13.050165      3.368718      4.201586  27513.990282   
omavalitsus      0.000000      0.000000      0.000000      0.000000   
osa             32.929018    334.182771    555.238397     55.224379   

                     kogu       kohalik          suur          pikk  \
aasta           31.860606      0.000000      0.000000   1223.457367   
aeg          24260.777251      0.000000      0.000000  14886.333675   
määrus           0.000000      0.000000      0.000000      0.000000   
omavalitsus      0.000000  24260.696867      0.000000      0.000000   
osa             20.587062      0.000000  22145.681025      0.000000   

             juriidiline         tulev  ...  realiseeritav  valgustatav  \
aasta                0.0  12627.573405  ...            0.0          0.0   
aeg                  0.0      0.000000  ...            0.0          0.0   
määrus               0.0      0.000000  ...            0.0          0.0   
omavalitsus          0.0      0.000000  ...            0.0          0.0   
osa                  0.0      0.000000  ...            0.0          0.0   

             vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  õigusetu  \
aasta          0.0               0.0                  0.0       0.0       0.0   
aeg            0.0               0.0                  0.0       0.0       0.0   
määrus         0.0               0.0                  0.0       0.0       0.0   
omavalitsus    0.0               0.0                  0.0       0.0       0.0   
osa            0.0               0.0                  0.0       0.0       0.0   

             oletuslik  raugematu  raudteeäärne  
aasta              0.0        0.0           0.0  
aeg                0.0        0.0           0.0  
määrus             0.0        0.0           0.0  
omavalitsus        0.0        0.0           0.0  
osa                0.0        0.0           0.0  

[5 rows x 7358 columns]

In [63]:
diff_df = data - dot_df

In [64]:
diff_df.head()

eelmine    järgmine     viimane     käesolev         kogu  \
aasta        412.864590  233.701801  241.223925  4421.775054  1083.139394   
aeg           75.000000   65.000000   32.948027  1227.000000   736.222749   
määrus         2.949835  106.631282   12.798414     0.009718    30.000000   
omavalitsus   30.000000   67.000000   44.000000     0.000000    31.000000   
osa          168.070982  101.817229  362.761603    62.775621    30.412938   

                 kohalik        suur        pikk  juriidiline      tulev  ...  \
aasta          40.000000  114.000000  338.542633          0.0   6.426595  ...   
aeg          1373.000000  194.000000   26.666325          0.0  18.000000  ...   
määrus          0.000000    0.000000    0.000000          0.0   0.000000  ...   
omavalitsus     0.303133   84.000000    0.000000         12.0   0.000000  ...   
osa            10.000000   19.318975   25.000000          0.0  17.000000  ...   

             realiseeritav  valgustatav  vajuv  väikesekasvuline  \
aasta                  0.0          0.0    0.0               0.0   
aeg                    0.0          0.0    0.0               0.0   
määrus                 0.0          0.0    0.0               0.0   
omavalitsus            0.0          0.0    0.0               0.0   
osa                    0.0          0.0    0.0               0.0   

             väikeseformaadiline  õlirikas  õigusetu  oletuslik  raugematu  \
aasta                        0.0       0.0       0.0        0.0        0.0   
aeg                          0.0       0.0       0.0        0.0        0.0   
määrus                       0.0       0.0       0.0        0.0        0.0   
omavalitsus                  0.0       0.0       0.0        0.0        0.0   
osa                          0.0       0.0       0.0        0.0        0.0   

             raudteeäärne  
aasta                 0.0  
aeg                   0.0  
määrus                0.0  
omavalitsus           0.0  
osa                   0.0  

[5 rows x 7358 columns]

-----

In [20]:
for i in range(1000):
    print(f"Topic number {i}, most common adjectives and scores:")
    print(adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("-----------------------------------")

Topic number 0, most common adjectives and scores:
eelmine     208.376391
järgmine    148.611746
viimane      93.410659
tulev        36.987329
läinud       18.329727
Name: 0, dtype: float64
-----------------------------------
Topic number 1, most common adjectives and scores:
viimane    130.988471
kogu       116.560595
pikk        69.678960
õige        40.349416
vaba        34.257144
Name: 1, dtype: float64
-----------------------------------
Topic number 2, most common adjectives and scores:
käesolev     219.777499
kõnealune      2.604750
käsitlev       2.335547
vastav         1.986746
muudetud       0.613056
Name: 2, dtype: float64
-----------------------------------
Topic number 3, most common adjectives and scores:
suur               168.105548
südamlik             0.103061
99protsendiline      0.035807
kaduvväike           0.023983
90protsendiline      0.021445
Name: 3, dtype: float64
-----------------------------------
Topic number 4, most common adjectives and scores:
kohalik   

täis           120.249103
hirmus           0.670779
enneolematu      0.666424
piisav           0.662363
hüva             0.563486
Name: 48, dtype: float64
-----------------------------------
Topic number 49, most common adjectives and scores:
punane            76.008275
valge              1.905687
tulipunane         0.406335
väikeseõieline     0.154428
suureõieline       0.115821
Name: 49, dtype: float64
-----------------------------------
Topic number 50, most common adjectives and scores:
endine     132.157561
uus         49.155082
tollane     35.995554
toonane     16.589576
vastne       8.326151
Name: 50, dtype: float64
-----------------------------------
Topic number 51, most common adjectives and scores:
rahaline    190.260624
riiklik      93.597989
antav        75.507979
tugev        63.851872
suur         62.860166
Name: 51, dtype: float64
-----------------------------------
Topic number 52, most common adjectives and scores:
lõplik         579.043557
õigeaegne        7.790754
j

Name: 106, dtype: float64
-----------------------------------
Topic number 107, most common adjectives and scores:
elukestev       25.193872
tasuline         7.429011
eestikeelne      5.646202
teoreetiline     4.198297
arvutipõhine     3.889519
Name: 107, dtype: float64
-----------------------------------
Topic number 108, most common adjectives and scores:
vasak    37.225872
oma      14.840929
karm     10.409565
tühi      9.763893
kõva      7.915542
Name: 108, dtype: float64
-----------------------------------
Topic number 109, most common adjectives and scores:
õige        125.732499
uus          96.925951
hea          80.086560
olnud        32.473500
võimalik     21.905291
Name: 109, dtype: float64
-----------------------------------
Topic number 110, most common adjectives and scores:
õiguslik          1015.011881
seadusandlik        12.955241
piisav              11.676359
keskkonnaalane       5.654871
küllaldane           5.537117
Name: 110, dtype: float64
------------------------

Name: 152, dtype: float64
-----------------------------------
Topic number 153, most common adjectives and scores:
selge        28.220273
terviklik     0.314337
ilmne         0.307575
ähmane        0.198648
väär          0.150714
Name: 153, dtype: float64
-----------------------------------
Topic number 154, most common adjectives and scores:
suuline        17.585836
teistkordne     1.482137
iga-aastane     0.717453
iidne           0.475784
korduv          0.463038
Name: 154, dtype: float64
-----------------------------------
Topic number 155, most common adjectives and scores:
vähene     74.898324
vajalik    55.261273
oluline    49.261636
piisav     33.836145
suur       13.529451
Name: 155, dtype: float64
-----------------------------------
Topic number 156, most common adjectives and scores:
ainuke       1212.591082
ainus         192.325126
tüüpiline      25.029338
mõistetav      18.268948
igavene        15.968446
Name: 156, dtype: float64
-----------------------------------
Topic nu

paks             205.244098
kevadine          11.905254
kinnisõidetud     11.884052
kohev              8.155080
mahasadanud        5.741733
Name: 228, dtype: float64
-----------------------------------
Topic number 229, most common adjectives and scores:
märg          88.751685
linane        34.471871
niiske        24.263576
puuvillane    21.800562
liibuv        14.528409
Name: 229, dtype: float64
-----------------------------------
Topic number 230, most common adjectives and scores:
ametkondlik       104.068715
teenistuslik       48.803535
ametlik            13.892822
teenistusalane      8.916558
põhjalik            7.513459
Name: 230, dtype: float64
-----------------------------------
Topic number 231, most common adjectives and scores:
tulevane     7.890597
armastav     0.498822
vastne       0.463932
hoolitsev    0.264449
ootav        0.237737
Name: 231, dtype: float64
-----------------------------------
Topic number 232, most common adjectives and scores:
luterlik      723.802228


...

kriitiline    26.178386
ühtlane        8.571203
viidatud       1.181415
püdel          1.085394
sültjas        1.085394
Name: 734, dtype: float64
-----------------------------------
Topic number 735, most common adjectives and scores:
kandev         39.133355
geniaalne      33.985560
algne          27.917456
originaalne    25.957153
uudne          19.267030
Name: 735, dtype: float64
-----------------------------------
Topic number 736, most common adjectives and scores:
kuuluv           61.180454
enamkaubeldud     0.511418
eraõiguslik       0.476057
osutav            0.380148
ühinev            0.349926
Name: 736, dtype: float64
-----------------------------------
Topic number 737, most common adjectives and scores:
strateegiline        321.288272
potentsiaalne        106.652357
välismaine            81.013547
võimalik              63.572338
institutsionaalne     54.054411
Name: 737, dtype: float64
-----------------------------------
Topic number 738, most common adjectives and scores:


Name: 777, dtype: float64
-----------------------------------
Topic number 778, most common adjectives and scores:
tuttav    169.847195
uus       120.497970
rõõmus    110.573731
morn       94.078647
hapu       82.096408
Name: 778, dtype: float64
-----------------------------------
Topic number 779, most common adjectives and scores:
must        54.780451
kroonine     7.731973
tekkiv       6.070490
suurune      5.906239
sügav        4.960644
Name: 779, dtype: float64
-----------------------------------
Topic number 780, most common adjectives and scores:
potentsiaalne    184.603816
võimalik          28.376307
rikas              9.748095
nõudlik            9.311202
kasutav            7.684986
Name: 780, dtype: float64
-----------------------------------
Topic number 781, most common adjectives and scores:
hele            158.261639
tume            134.942218
kange           105.972918
alkoholivaba     93.754545
lahja            87.853694
Name: 781, dtype: float64
------------------------

Name: 821, dtype: float64
-----------------------------------
Topic number 822, most common adjectives and scores:
väidetav    114.852437
jäme         75.044486
korduv       68.870023
ilmne        54.527946
räige        18.801952
Name: 822, dtype: float64
-----------------------------------
Topic number 823, most common adjectives and scores:
õnnetu     469.598939
taevane    201.821735
maine      189.359816
kirglik    121.541467
igavene     86.003172
Name: 823, dtype: float64
-----------------------------------
Topic number 824, most common adjectives and scores:
vaba        196.586070
tasuv        34.284552
vakantne     25.593963
loodav       17.831679
nõudev       17.642461
Name: 824, dtype: float64
-----------------------------------
Topic number 825, most common adjectives and scores:
märgitud            357.609043
paaritu              42.673011
kindlaksmääratud     29.333637
välismaine           25.463018
kajastav             23.921750
Name: 825, dtype: float64
-------------------

anonüümne        199.140475
usaldusväärne    165.935461
seisev            59.736510
lähedalseisev     45.351411
sooviv            40.198223
Name: 891, dtype: float64
-----------------------------------
Topic number 892, most common adjectives and scores:
vastav         152.243677
ametlik        140.481510
poliitiline    135.049803
eilne          114.770460
uus             71.024417
Name: 892, dtype: float64
-----------------------------------
Topic number 893, most common adjectives and scores:
parempoolne             109.944968
sotsiaaldemokraatlik    102.236702
konservatiivne           39.103867
vasakpoolne              28.723885
tekkiv                   19.566353
Name: 893, dtype: float64
-----------------------------------
Topic number 894, most common adjectives and scores:
viimane         91.089854
järgmine        73.033380
uus             50.078168
olnud           10.657389
samanimeline     1.558815
Name: 894, dtype: float64
-----------------------------------
Topic number 895, 

vabakutseline      142.160802
professionaalne     51.918429
andekas             31.058831
nimekas             31.049165
külmetav            27.137334
Name: 965, dtype: float64
-----------------------------------
Topic number 966, most common adjectives and scores:
relvataoline      42.369322
püstolitaoline    34.192786
väärtuslik        17.491332
kahtlane          15.034905
maagiline         14.807157
Name: 966, dtype: float64
-----------------------------------
Topic number 967, most common adjectives and scores:
keedetud         121.751090
toores            26.965667
koorimata         13.602632
pruun             11.412087
lahtiklopitud     10.980842
Name: 967, dtype: float64
-----------------------------------
Topic number 968, most common adjectives and scores:
sotsiaalne           74.254670
sajaprotsendiline     1.712573
riigipoolne           0.627892
10aastane             0.478845
kümneaastane          0.452208
Name: 968, dtype: float64
-----------------------------------
Topic nu

#### Colours

In [21]:
colours = ['valge', 'kollane', 'oranž', 'roosa', 'punane', 'pruun', 'roheline', 'sinine', 'lilla', 'hall', 'must']

In [22]:
adjs_in_topics[colours]

valge  kollane  oranž     roosa    punane  pruun  roheline  sinine  \
0    0.000000      0.0    0.0  0.000000  0.001920    0.0  0.000000     0.0   
1    1.771836      0.0    0.0  0.000000  0.137335    0.0  0.028813     0.0   
2    0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
3    0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
4    0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
..        ...      ...    ...       ...       ...    ...       ...     ...   
995  0.000000      0.0    0.0  0.302837  0.000000    0.0  0.003271     0.0   
996  0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
997  0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
998  0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   
999  0.000000      0.0    0.0  0.000000  0.000000    0.0  0.000000     0.0   

     lilla      hall      must  
0      0.0  0.000000  0.000000  
1      0.0  0.619015  0.058042  
2      0.0  0.000000  0.000000  
3      0.0  0.000000  0.000000  
4      0.0  0.000000  0.000000  
..     ...       ...       ...  
995    0.0  0.000000  0.000000  
996    0.0  0.000000  0.000000  
997    0.0  0.000000  0.000000  
998    0.0  0.000000  0.000000  
999    0.0  0.000000  0.000000  

[1000 rows x 11 columns]

In [200]:
for colour in colours:
    print(f"Värv '{colour}'")
    col_topics = adjs_in_topics[colour][adjs_in_topics[colour] > 0].sort_values(ascending=False)
    print(f"Number of topics with pseudocount > 0 (default) is {len(col_topics)}")
    print(col_topics.head(10))
    print("-------------------------")

Värv 'valge'
Number of topics with pseudocount > 0 (default) is 72
117    502.624990
348    262.158179
831     88.718048
23      67.672624
751     50.148131
972     49.889762
283     47.532032
834     43.727873
29      37.499017
696     24.112011
Name: valge, dtype: float64
-------------------------
Värv 'kollane'
Number of topics with pseudocount > 0 (default) is 50
140    94.882871
834    56.720694
459    27.571868
466     6.674576
811     6.627886
348     6.353998
239     5.991258
827     5.547321
389     4.774305
29      3.986103
Name: kollane, dtype: float64
-------------------------
Värv 'oranž'
Number of topics with pseudocount > 0 (default) is 28
146    5.952164
64     1.721803
811    1.667117
239    0.887454
340    0.818592
690    0.736530
229    0.570000
588    0.479897
911    0.372560
140    0.163938
Name: oranž, dtype: float64
-------------------------
Värv 'roosa'
Number of topics with pseudocount > 0 (default) is 65
646    12.962255
972    12.374072
503     9.311642
466  

In [228]:
colours_topics = defaultdict(list)

for colour in colours:
    col_topics = adjs_in_topics[colour].sort_values(ascending=False).head(3)
    for index in col_topics.index:
        colours_topics[index].append(colour)

In [229]:
colours_topics

defaultdict(list,
            {117: ['valge'],
             348: ['valge', 'must'],
             831: ['valge', 'pruun', 'hall'],
             140: ['kollane'],
             834: ['kollane'],
             459: ['kollane'],
             146: ['oranž'],
             64: ['oranž', 'lilla'],
             811: ['oranž', 'lilla'],
             646: ['roosa'],
             972: ['roosa'],
             503: ['roosa'],
             470: ['punane'],
             49: ['punane'],
             389: ['punane'],
             466: ['pruun', 'sinine', 'hall'],
             588: ['pruun'],
             667: ['roheline'],
             847: ['roheline'],
             802: ['roheline', 'must'],
             542: ['sinine'],
             75: ['sinine'],
             786: ['lilla'],
             226: ['hall'],
             65: ['must']})

In [231]:
for lbl in colours_topics.keys():
    print(colours_topics[lbl], topics[lbl])

['valge'] []
['valge', 'must'] []
['valge', 'pruun', 'hall'] []
['kollane'] ['kaart', 'liidrisärk']
['kollane'] []
['kollane'] []
['oranž'] ['revolutsioon', 'kitarrist']
['oranž', 'lilla'] ['nahktagi', 'katk']
['oranž', 'lilla'] []
['roosa'] []
['roosa'] []
['roosa'] ['üksindus']
['punane'] []
['punane'] ['rist', 'tuli', 'latern', 'planeet', 'foorituli', 'tellis', 'paprika', 'kurat', 'põsk', 'brigaad', 'huulepulk', 'kork', 'telliskivi', 'kõrb']
['punane'] []
['pruun', 'sinine', 'hall'] []
['pruun'] []
['roheline'] ['aas', 'konn', 'mõttelaad']
['roheline'] []
['roheline', 'must'] []
['sinine'] ['vilkur', 'silmaalune', 'teksad', 'salong', 'teksased', 'muhk', 'tass', 'samet', 'teemant', 'dressipüksid']
['sinine'] []
['lilla'] []
['hall'] []
['must'] ['komöödia', 'valge', 'prügikott', 'kassa', 'kulm']


In [232]:
colours_topics_max = defaultdict(list)

for colour in colours:
    col_topics = adjs_in_topics[colour].sort_values(ascending=False).head(1)
    for index in col_topics.index:
        colours_topics_max[index].append(colour)

In [234]:
colours_topics_max

defaultdict(list,
            {117: ['valge'],
             140: ['kollane'],
             146: ['oranž'],
             646: ['roosa'],
             470: ['punane'],
             466: ['pruun', 'sinine'],
             667: ['roheline'],
             64: ['lilla'],
             831: ['hall'],
             802: ['must']})

In [235]:
for cls, col in colours_topics_max.items():
    print("colours:", col)
    print(adjs_in_topics.loc[cls].sort_values(ascending=False).head(10))
    print("--------------")

colours: ['valge']
poliitiline     93252.334038
vääramatu       24199.038627
tagasiulatuv     9014.923650
suur             8199.802526
oma              8169.098592
liikumapanev     7335.926001
edasiviiv        5966.881802
täis             5884.802561
kogu             5144.979506
sõjaline         5084.146754
Name: 117, dtype: float64
--------------
colours: ['kollane']
kollane            94.882871
visa                4.710129
ambulatoorne        4.369523
topograafiline      3.551668
trükitud            1.791907
digitaalne          1.222482
topoloogiline       1.166825
kolmemõõtmeline     0.816992
geomeetriline       0.803842
interaktiivne       0.587737
Name: 140, dtype: float64
--------------
colours: ['oranž']
laulev            39.097433
oranž              5.952164
suur               1.364285
uus                1.075348
sotsialistlik      1.065767
värviline          0.985063
tõeline            0.984826
tehnoloogiline     0.824648
tööstuslik         0.714106
rahumeelne         0.550874

In [238]:
nouns_in_topics[466].sort_values(ascending=False).head(10)

silm       1.729471
värvus     0.038366
jume       0.032816
riis       0.027254
laik       0.022614
king       0.016113
triip      0.015911
vedelik    0.012074
ülikond    0.011098
katk       0.010044
Name: 466, dtype: float64

In [217]:
topics[140]

['kaart', 'liidrisärk']

In [209]:
adjs_in_topics.loc[117]['valge']

502.62499040992157

In [210]:
adjs_in_topics['valge'].sort_values(ascending=False)

117    502.624990
348    262.158179
831     88.718048
23      67.672624
751     50.148131
          ...    
649      0.000000
648      0.000000
647      0.000000
646      0.000000
0        0.000000
Name: valge, Length: 1000, dtype: float64

#### midagi muud

In [26]:
results

array([[2.54185504e+02, 9.86174015e-02, 1.44129710e+01, ...,
        0.00000000e+00, 2.89740022e-01, 0.00000000e+00],
       [0.00000000e+00, 2.08329613e+02, 3.72552389e+00, ...,
        0.00000000e+00, 1.39599629e-02, 0.00000000e+00],
       [2.95838552e-04, 0.00000000e+00, 1.14458812e+02, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       ...,
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00]])

In [28]:
all_in_topic = []
for i, result in enumerate(results):
    if result[842] > 0:
        all_in_topic.append(data.index[i])

In [29]:
print(len(all_in_topic), "words:", all_in_topic)

199 words: ['konkurss', 'hääl', 'käive', 'osakond', 'maitse', 'uks', 'kast', 'klubi', 'huumor', 'väljak', 'parkla', 'toon', 'püks', 'nahk', 'veri', 'positsioon', 'pidu', 'autasu', 'haigla', 'laik', 'tsoon', 'tseremoonia', 'kuld', 'ilme', 'alkoholisisaldus', 'liidrisärk', 'nõudmine', 'ülikond', 'võti', 'leek', 'emissioon', 'valgus', 'kohtuprotsess', 'lennuväli', 'soovitus', 'fond', 'pluus', 'arvutus', 'mahl', 'majandustulemus', 'aktsiaemissioon', 'nuga', 'ümbrik', 'lokk', 'prill', 'nõuanne', 'teenetemärk', 'mantel', 'vabandus', 'sein', 'triip', 'king', 'nõupidamine', 'riis', 'pakk', 'rukkilill', 'riietus', 'hoidmine', 'väljend', 'kuulutamine', 'kommentaar', 'kohtuistung', 'karv', 'formaat', 'olemine', 'kontrast', 'palve', 'muie', 'pankrot', 'tuluke', 'pulm', 'kõneviis', 'varjund', 'poleemika', 'värvus', 'kohtunik', 'tõdemus', 'madalseis', 'jope', 'põld', 'tenor', 'mesi', 'panter', 'liikleja', 'triiksärk', 'sõiduvahend', 'luu', 'laks', 'värss', 'nahktagi', 'olelusvõitlus', 'jume', 'padi'

In [43]:
a = np.array([1, 5, 2, 10, 92, 3, 1000])

In [44]:
a

array([   1,    5,    2,   10,   92,    3, 1000])

In [47]:
3 in np.argpartition(a, -3)[-3:]

True

In [46]:
a

array([   1,    5,    2,   10,   92,    3, 1000])

In [48]:
max_in_topic = []
for i, result in enumerate(results):
    if 842 in np.argpartition(result, -3)[-3:]:
        max_in_topic.append(data.index[i])

In [49]:
print(len(max_in_topic), "words:", max_in_topic)

4 words: ['kõneviis', 'narmasnutt', 'retuusid', 'kleidike']


In [51]:
data.loc['kõneviis']

eelmine         0
järgmine        0
viimane         0
käesolev        0
kogu            0
               ..
õlirikas        0
õigusetu        0
oletuslik       0
raugematu       0
raudteeäärne    0
Name: kõneviis, Length: 7442, dtype: int64

In [56]:
data.loc['kõneviis']['eelmine']

0

In [57]:
for adj in data.loc['kõneviis'].index:
    if adj in colours:
        print(adj, data.loc['kõneviis'][adj])

valge 0
kollane 0
punane 0
must 0
roheline 0
sinine 0
hall 0
pruun 0
oranž 0
roosa 0
lilla 0


In [58]:
for i in range(len(data.index)):
    if data.index[i] == 'kõneviis':
        print(i)
        break

3125


In [60]:
results[3125][842]

0.006707453226342392

In [62]:
data.loc['kõneviis'].sort_values(ascending=False).head()

tingiv          71
kindel          60
käskiv          52
kaudne          16
raudteeäärne     0
Name: kõneviis, dtype: int64

In [65]:
adjs_in_topics.loc[842][['tingiv', 'kindel', 'käskiv', 'kaudne']]

tingiv     0.163827
kindel     0.000000
käskiv    14.873369
kaudne     0.000000
Name: 842, dtype: float64

### See asi

In [107]:
adjs_topics = adjs_in_topics.copy()

In [108]:
adjs_topics.values

array([[2.07336414e+02, 1.48653077e+02, 9.36812008e+01, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [2.35085414e-02, 2.15587121e-02, 1.30746802e+02, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 8.12906684e-02, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       ...,
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00]])

In [109]:
adjs_topics.max(axis=1)

0      207.336414
1      130.746802
2      219.165518
3      167.968476
4      159.520785
          ...    
995     12.275288
996     93.823105
997     19.074055
998     17.354936
999     37.081552
Length: 1000, dtype: float64

In [110]:
adjs_topics.loc[0].max()

207.33641371086486

In [111]:
for i in adjs_topics.index:
    adjs_topics.loc[i][adjs_topics.loc[i] * 10 < adjs_topics.loc[i].max()] = 0

In [112]:
adjs_topics

eelmine    järgmine     viimane    käesolev        kogu     kohalik  \
0    207.336414  148.653077   93.681201   21.384637    0.000000    0.000000   
1      0.000000    0.000000  130.746802    0.000000  116.376795    0.000000   
2      0.000000    0.000000    0.000000  219.165518    0.000000    0.000000   
3      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
4      0.000000    0.000000    0.000000    0.000000    0.000000  159.520785   
..          ...         ...         ...         ...         ...         ...   
995    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
996    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
997    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
998    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   
999    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   

           suur       pikk  juriidiline      tulev  ...  realiseeritav  \
0      0.000000   0.000000          0.0  40.947601  ...            0.0   
1      0.000000  69.304617          0.0   0.000000  ...            0.0   
2      0.000000   0.000000          0.0   0.000000  ...            0.0   
3    167.968476   0.000000          0.0   0.000000  ...            0.0   
4      0.000000   0.000000          0.0   0.000000  ...            0.0   
..          ...        ...          ...        ...  ...            ...   
995    0.000000   0.000000          0.0   0.000000  ...            0.0   
996    0.000000   0.000000          0.0   0.000000  ...            0.0   
997    0.000000   0.000000          0.0   0.000000  ...            0.0   
998    0.000000   0.000000          0.0   0.000000  ...            0.0   
999    0.000000   0.000000          0.0   0.000000  ...            0.0   

     valgustatav  vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  \
0            0.0    0.0               0.0                  0.0       0.0   
1            0.0    0.0               0.0                  0.0       0.0   
2            0.0    0.0               0.0                  0.0       0.0   
3            0.0    0.0               0.0                  0.0       0.0   
4            0.0    0.0               0.0                  0.0       0.0   
..           ...    ...               ...                  ...       ...   
995          0.0    0.0               0.0                  0.0       0.0   
996          0.0    0.0               0.0                  0.0       0.0   
997          0.0    0.0               0.0                  0.0       0.0   
998          0.0    0.0               0.0                  0.0       0.0   
999          0.0    0.0               0.0                  0.0       0.0   

     õigusetu  oletuslik  raugematu  raudteeäärne  
0         0.0        0.0        0.0           0.0  
1         0.0        0.0        0.0           0.0  
2         0.0        0.0        0.0           0.0  
3         0.0        0.0        0.0           0.0  
4         0.0        0.0        0.0           0.0  
..        ...        ...        ...           ...  
995       0.0        0.0        0.0           0.0  
996       0.0        0.0        0.0           0.0  
997       0.0        0.0        0.0           0.0  
998       0.0        0.0        0.0           0.0  
999       0.0        0.0        0.0           0.0  

[1000 rows x 7442 columns]

In [118]:
nouns_topics = nouns_in_topics.copy()

In [122]:
nouns_topics.columns

RangeIndex(start=0, stop=1000, step=1)

In [123]:
for i in nouns_topics.columns:
    nouns_topics[i][nouns_topics[i] * 10 < nouns_topics[i].max()] = 0

In [124]:
nouns_topics

0           1           2           3           4    \
aasta          254.185504    0.000000   14.412971    0.000000    0.000000   
aeg              0.000000  208.329613    0.000000    0.000000    0.000000   
määrus           0.000000    0.000000  114.458812    0.000000    0.000000   
omavalitsus      0.000000    0.000000    0.000000    0.000000  152.086404   
osa              0.000000    0.000000    0.000000  131.695535    0.000000   
...                   ...         ...         ...         ...         ...   
eelekspertiis    0.000000    0.000000    0.000000    0.000000    0.000000   
amatöörfilm      0.000000    0.000000    0.000000    0.000000    0.000000   
võimeteproov     0.000000    0.000000    0.000000    0.000000    0.000000   
filmiauhind      0.000000    0.000000    0.000000    0.000000    0.000000   
filmikriitik     0.000000    0.000000    0.000000    0.000000    0.000000   

               5    6          7    8    9    ...  990  991  992  993  994  \
aasta          0.0  0.0  17.167730  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
aeg            0.0  0.0   3.863264  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
määrus         0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
omavalitsus    0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
osa            0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
...            ...  ...        ...  ...  ...  ...  ...  ...  ...  ...  ...   
eelekspertiis  0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
amatöörfilm    0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
võimeteproov   0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
filmiauhind    0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   
filmikriitik   0.0  0.0   0.000000  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0   

               995       996  997  998  999  
aasta          0.0  1.245986  0.0  0.0  0.0  
aeg            0.0  0.000000  0.0  0.0  0.0  
määrus         0.0  0.000000  0.0  0.0  0.0  
omavalitsus    0.0  0.000000  0.0  0.0  0.0  
osa            0.0  0.000000  0.0  0.0  0.0  
...            ...       ...  ...  ...  ...  
eelekspertiis  0.0  0.000000  0.0  0.0  0.0  
amatöörfilm    0.0  0.000000  0.0  0.0  0.0  
võimeteproov   0.0  0.000000  0.0  0.0  0.0  
filmiauhind    0.0  0.000000  0.0  0.0  0.0  
filmikriitik   0.0  0.000000  0.0  0.0  0.0  

[14590 rows x 1000 columns]

In [129]:
dot_val = np.dot(nouns_topics, adjs_topics)

In [130]:
dot_val.shape

(14590, 7442)

In [131]:
dot_df = pd.DataFrame(dot_val, index=data.index, columns=data.columns)

In [132]:
dot_df

eelmine      järgmine       viimane      käesolev  \
aasta          52782.671693  37848.018338  23812.403237  11763.706853   
aeg                0.000000      0.000000  27877.166485      0.000000   
määrus             0.000000      0.000000      0.000000  27513.902704   
omavalitsus        0.000000      0.000000      0.000000      0.000000   
osa               48.864496    393.251460    455.077197      0.000000   
...                     ...           ...           ...           ...   
eelekspertiis      0.000000      0.000000      0.000000      0.000000   
amatöörfilm        0.000000      0.000000      0.000000      0.000000   
võimeteproov       0.000000      0.000000      0.000000      0.000000   
filmiauhind        0.000000      0.000000      0.000000      0.000000   
filmikriitik       0.000000      0.000000      0.000000      0.000000   

                       kogu       kohalik          suur          pikk  \
aasta             77.919178      0.000000      0.000000   1146.997826   
aeg            24370.760218      0.000000      0.000000  14907.464231   
määrus            29.984233      0.000000      0.000000      0.000000   
omavalitsus        0.000000  24260.942638      0.000000      0.000000   
osa               50.912592      0.000000  22120.698285      0.000000   
...                     ...           ...           ...           ...   
eelekspertiis      0.000000      0.000000      0.000000      0.000000   
amatöörfilm        0.000000      0.000000      0.000000      0.000000   
võimeteproov       0.000000      0.000000      0.000000      0.000000   
filmiauhind        0.000000      0.000000      0.000000      0.000000   
filmikriitik       0.000000      0.000000      0.000000      0.000000   

               juriidiline         tulev  ...  realiseeritav  valgustatav  \
aasta                  0.0  12625.848996  ...            0.0          0.0   
aeg                    0.0      0.000000  ...            0.0          0.0   
määrus                 0.0      0.000000  ...            0.0          0.0   
omavalitsus            0.0      0.000000  ...            0.0          0.0   
osa                    0.0      0.000000  ...            0.0          0.0   
...                    ...           ...  ...            ...          ...   
eelekspertiis          0.0      0.000000  ...            0.0          0.0   
amatöörfilm            0.0      0.000000  ...            0.0          0.0   
võimeteproov           0.0      0.000000  ...            0.0          0.0   
filmiauhind            0.0      0.000000  ...            0.0          0.0   
filmikriitik           0.0      0.000000  ...            0.0          0.0   

               vajuv  väikesekasvuline  väikeseformaadiline  õlirikas  \
aasta            0.0               0.0                  0.0       0.0   
aeg              0.0               0.0                  0.0       0.0   
määrus           0.0               0.0                  0.0       0.0   
omavalitsus      0.0               0.0                  0.0       0.0   
osa              0.0               0.0                  0.0       0.0   
...              ...               ...                  ...       ...   
eelekspertiis    0.0               0.0                  0.0       0.0   
amatöörfilm      0.0               0.0                  0.0       0.0   
võimeteproov     0.0               0.0                  0.0       0.0   
filmiauhind      0.0               0.0                  0.0       0.0   
filmikriitik     0.0               0.0                  0.0       0.0   

               õigusetu  oletuslik  raugematu  raudteeäärne  
aasta               0.0        0.0        0.0           0.0  
aeg                 0.0        0.0        0.0           0.0  
määrus              0.0        0.0        0.0           0.0  
omavalitsus         0.0        0.0        0.0           0.0  
osa                 0.0        0.0        0.0           0.0  
...                 ...        ...        ...           ...  
eelekspertiis       0.0       

In [134]:
diff_df = data - dot_df

In [135]:
diff_df

eelmine    järgmine     viimane     käesolev         kogu  \
aasta          467.328307  258.981662  597.596763   -10.706853  1037.080822   
aeg             75.000000   65.000000   37.833515  1227.000000   626.239782   
määrus          16.000000  110.000000   17.000000     0.097296     0.015767   
omavalitsus     30.000000   67.000000   44.000000     0.000000    31.000000   
osa            152.135504   42.748540  462.922803   118.000000     0.087408   
...                   ...         ...         ...          ...          ...   
eelekspertiis    0.000000    0.000000    0.000000     0.000000     0.000000   
amatöörfilm      0.000000    0.000000    0.000000     0.000000     0.000000   
võimeteproov     0.000000    0.000000    0.000000     0.000000     0.000000   
filmiauhind      0.000000    0.000000    0.000000     0.000000     0.000000   
filmikriitik     0.000000    0.000000    0.000000     0.000000     0.000000   

                   kohalik        suur        pikk  juriidiline      tulev  \
aasta            40.000000  114.000000  415.002174          0.0   8.151004   
aeg            1373.000000  194.000000    5.535769          0.0  18.000000   
määrus            0.000000    0.000000    0.000000          0.0   0.000000   
omavalitsus       0.057362   84.000000    0.000000         12.0   0.000000   
osa              10.000000   44.301715   25.000000          0.0  17.000000   
...                    ...         ...         ...          ...        ...   
eelekspertiis     0.000000    0.000000    0.000000          0.0   0.000000   
amatöörfilm       0.000000    0.000000    0.000000          0.0   0.000000   
võimeteproov      0.000000    0.000000    0.000000          0.0   0.000000   
filmiauhind       0.000000    0.000000    0.000000          0.0   0.000000   
filmikriitik      0.000000    0.000000    0.000000          0.0   0.000000   

               ...  realiseeritav  valgustatav  vajuv  väikesekasvuline  \
aasta          ...            0.0          0.0    0.0               0.0   
aeg            ...            0.0          0.0    0.0               0.0   
määrus         ...            0.0          0.0    0.0               0.0   
omavalitsus    ...            0.0          0.0    0.0               0.0   
osa            ...            0.0          0.0    0.0               0.0   
...            ...            ...          ...    ...               ...   
eelekspertiis  ...            0.0          0.0    0.0               0.0   
amatöörfilm    ...            0.0          0.0    0.0               0.0   
võimeteproov   ...            0.0          0.0    0.0               0.0   
filmiauhind    ...            0.0          0.0    0.0               0.0   
filmikriitik   ...            0.0          0.0    0.0               0.0   

               väikeseformaadiline  õlirikas  õigusetu  oletuslik  raugematu  \
aasta                          0.0       0.0       0.0        0.0        0.0   
aeg                            0.0       0.0       0.0        0.0        0.0   
määrus                         0.0       0.0       0.0        0.0        0.0   
omavalitsus                    0.0       0.0       0.0        0.0        0.0   
osa                            0.0       0.0       0.0        0.0        0.0   
...                            ...       ...       ...        ...        ...   
eelekspertiis                  0.0       0.0       0.0        0.0        0.0   
amatöörfilm                    0.0       0.0       0.0        0.0        0.0   
võimeteproov                   0.0       0.0       0.0        0.0        0.0   
filmiauhind                    0.0       0.0       0.0        0.0        0.0   
filmikriitik                   0.0       0.0       0.0        0.0        0.0   

               raudteeäärne  
aasta                   0.0  
aeg                     0.0  
määrus                  0.0  
omavalitsus             0.0  
osa                     0.0  
...                     ...  
eelekspertiis           0.0  
amatöörfilm             0.0  


In [145]:
diff_pos = diff_df.copy()

In [146]:
diff_pos[diff_pos.lt(0)] = 0

In [176]:
diff_df.min().sort_values().head()

käesolev     -82.344273
taimne       -79.561519
elukestev    -76.515544
tööstuslik   -75.571046
kehaväline   -68.935183
dtype: float64

#### Exploration of diff dataset

In [209]:
diff_pairs = {}
for idx, row in diff_pos.iterrows():
    diff_pairs[idx] = list(row[row > 50].index)
    print("noun:", idx,"\ntop 5 adjectives:" , list(row[row > 50].sort_values(ascending=False).head().index))
    print("------------------------------")

noun: aasta 
top 5 adjectives: ['uus', 'läinud', 'terve', 'järgnev', 'olnud']
------------------------------
noun: aeg 
top 5 adjectives: ['olnud', 'raske', 'praegune', 'hea', 'kohalik']
------------------------------
noun: määrus 
top 5 adjectives: ['käsitlev', 'uus', 'vastav', 'kehtetu', 'kõnealune']
------------------------------
noun: omavalitsus 
top 5 adjectives: ['uus', 'väike', 'suur', 'sügisene', 'järgmine']
------------------------------
noun: osa 
top 5 adjectives: ['viimane', 'arvestatav', 'sissejuhatav', 'keskne', 'keskmine']
------------------------------
noun: tänu 
top 5 adjectives: ['eriline']
------------------------------
noun: nädal 
top 5 adjectives: ['läinud', 'uus', 'järgmine', 'terve', 'ülemöödunud']
------------------------------
noun: isik 
top 5 adjectives: ['eraõiguslik', 'olev', 'seotud', 'vastutav', 'konkreetne']
------------------------------
noun: maailm 
top 5 adjectives: ['terve', 'suur', 'muutuv', 'ülejäänud', 'globaliseeruv']
------------------------

noun: jook 
top 5 adjectives: ['kuum', 'hea', 'kange', 'lahja', 'joovastav']
------------------------------
noun: tähelepanu 
top 5 adjectives: ['suur', 'avalik', 'rahvusvaheline', 'kogu', 'oluline']
------------------------------
noun: hind 
top 5 adjectives: ['vaba', 'kindel', 'olnud', 'kõnealune', 'ränk']
------------------------------
noun: roll 
top 5 adjectives: ['suur', 'hea', 'väike', 'peamine', 'oluline']
------------------------------
noun: süsteem 
top 5 adjectives: ['kogu', 'praegune', 'võimalik', 'suur', 'rahvusvaheline']
------------------------------
noun: nimi 
top 5 adjectives: ['hea', 'suur', 'vana', 'ajalooline', 'seotud']
------------------------------
noun: koostöö 
top 5 adjectives: ['rahvusvaheline', 'majanduslik', 'hea', 'vajalik', 'vastastikune']
------------------------------
noun: eeskiri 
top 5 adjectives: ['uus', 'ühine', 'käesolev', 'ettenähtud', 'järgmine']
------------------------------
noun: vesi 
top 5 adjectives: ['keedetud', 'värske', 'olnud', 'hea',

noun: kohustus 
top 5 adjectives: ['ettenähtud', 'kirjalik', 'pikaajaline', 'vastav', 'lühiajaline']
------------------------------
noun: uudis 
top 5 adjectives: ['hea', 'meeldiv', 'huvitav', 'rõõmus', 'puudutav']
------------------------------
noun: kohtumine 
top 5 adjectives: ['viimane', 'eelmine', 'kogu', 'tänane', 'terve']
------------------------------
noun: peaminister 
top 5 adjectives: ['lugupeetud', 'eelmine', 'järgmine', 'toonane', 'lahkuv']
------------------------------
noun: tänav 
top 5 adjectives: ['uus', 'punane', 'tühi', 'aiaäärne', 'vaikne']
------------------------------
noun: tunne 
top 5 adjectives: ['hea', 'olnud', 'positiivne', 'rahvuslik', 'tõeline']
------------------------------
noun: esimees 
top 5 adjectives: ['eelmine', 'kogu', 'viimane']
------------------------------
noun: plaan 
top 5 adjectives: ['suur', 'uus', 'hea', 'isiklik', 'rahvusvaheline']
------------------------------
noun: kaamera 
top 5 adjectives: ['uus', 'hea']
---------------------------

noun: turg 
top 5 adjectives: ['kohalik', 'suur', 'väike', 'kogu', 'olnud']
------------------------------
noun: protokoll 
top 5 adjectives: ['käesolev', 'kõnealune']
------------------------------
noun: risk 
top 5 adjectives: ['suur', 'väike', 'kõrge', 'majanduslik', 'sotsiaalne']
------------------------------
noun: laen 
top 5 adjectives: ['mõeldud', 'madalaprotsendiline', 'regionaalpoliitiline', 'vana', 'odav']
------------------------------
noun: seisukoht 
top 5 adjectives: ['uus', 'praegune', 'tähtis', 'kirjalik', 'kõhklev']
------------------------------
noun: ring 
top 5 adjectives: ['suur', 'lai', 'väike', 'eelmine', 'kilomeetrine']
------------------------------
noun: põllumajanduspoliitika 
top 5 adjectives: []
------------------------------
noun: teave 
top 5 adjectives: ['kogu', 'avalik', 'järgmine', 'üksikasjalik', 'vastav']
------------------------------
noun: värv 
top 5 adjectives: ['uus', 'vana', 'õige', 'hea', 'värske']
------------------------------
noun: koossei

noun: kirik 
top 5 adjectives: ['uus', 'vana', 'asuv', 'kohalik', 'olnud']
------------------------------
noun: lava 
top 5 adjectives: ['suur', 'väike', 'vaba', 'uus', 'tühi']
------------------------------
noun: lipp 
top 5 adjectives: ['valge', 'must', 'kollane', 'uus', 'roheline']
------------------------------
noun: register 
top 5 adjectives: ['avalik', 'uus']
------------------------------
noun: poliitika 
top 5 adjectives: ['suur', 'rahvusvaheline', 'avalik', 'ühine', 'kohalik']
------------------------------
noun: lepe 
top 5 adjectives: ['rahvusvaheline', 'uus', 'rahvuslik', 'vaheline']
------------------------------
noun: saatus 
top 5 adjectives: ['õnnetu', 'olnud', 'teadmata', 'edaspidine']
------------------------------
noun: omand 
top 5 adjectives: ['isiklik', 'riiklik', 'ühine']
------------------------------
noun: tähtaeg 
top 5 adjectives: ['viimane', 'ettenähtud', 'keskmine', 'järgmine', 'pikk']
------------------------------
noun: enesetunne 
top 5 adjectives: ['he

...

top 5 adjectives: []
------------------------------
noun: wifi 
top 5 adjectives: []
------------------------------
noun: käitumisakt 
top 5 adjectives: []
------------------------------
noun: otepäälanna 
top 5 adjectives: []
------------------------------
noun: finantseerimisvõimalus 
top 5 adjectives: []
------------------------------
noun: ülalpeetav 
top 5 adjectives: []
------------------------------
noun: äädikas 
top 5 adjectives: []
------------------------------
noun: valuutakokkulepe 
top 5 adjectives: []
------------------------------
noun: IP-aadress 
top 5 adjectives: []
------------------------------
noun: meelelahutusmäng 
top 5 adjectives: []
------------------------------
noun: ümberpaiknemine 
top 5 adjectives: []
------------------------------
noun: väljundtabel 
top 5 adjectives: []
------------------------------
noun: vastandumine 
top 5 adjectives: []
------------------------------
noun: lisamärkus 
top 5 adjectives: []
------------------------------
noun: kapral

noun: jäetu 
top 5 adjectives: []
------------------------------
noun: biogaas 
top 5 adjectives: []
------------------------------
noun: säästueelarve 
top 5 adjectives: []
------------------------------
noun: Oscari-gala 
top 5 adjectives: []
------------------------------
noun: eelkõneleja 
top 5 adjectives: []
------------------------------
noun: identifitseerimine 
top 5 adjectives: []
------------------------------
noun: infomess 
top 5 adjectives: []
------------------------------
noun: arheoloog 
top 5 adjectives: []
------------------------------
noun: istandus 
top 5 adjectives: []
------------------------------
noun: filmitäht 
top 5 adjectives: []
------------------------------
noun: toiduõli 
top 5 adjectives: []
------------------------------
noun: lauatelefon 
top 5 adjectives: []
------------------------------
noun: algusaeg 
top 5 adjectives: []
------------------------------
noun: asjandus 
top 5 adjectives: []
------------------------------
noun: sõnastamine 
top 5 a

noun: maailmaturnee 
top 5 adjectives: []
------------------------------
noun: stardikoht 
top 5 adjectives: []
------------------------------
noun: laenukohustus 
top 5 adjectives: []
------------------------------
noun: topeltvoor 
top 5 adjectives: []
------------------------------
noun: kaldtee 
top 5 adjectives: []
------------------------------
noun: poistebänd 
top 5 adjectives: []
------------------------------
noun: tehnikaime 
top 5 adjectives: []
------------------------------
noun: paremerakond 
top 5 adjectives: []
------------------------------
noun: valiksari 
top 5 adjectives: []
------------------------------
noun: tots 
top 5 adjectives: []
------------------------------
noun: vormisolek 
top 5 adjectives: []
------------------------------
noun: koolitusluba 
top 5 adjectives: []
------------------------------
noun: kramp 
top 5 adjectives: []
------------------------------
noun: mõõdistustöö 
top 5 adjectives: []
------------------------------
noun: sekkumisvõi 
top 

noun: kolesteatoom 
top 5 adjectives: []
------------------------------
noun: mobiilsidefirma 
top 5 adjectives: []
------------------------------
noun: atašee 
top 5 adjectives: []
------------------------------
noun: lipik 
top 5 adjectives: []
------------------------------
noun: produktiivvõrse 
top 5 adjectives: []
------------------------------
noun: kõhnumine 
top 5 adjectives: []
------------------------------
noun: lõimis 
top 5 adjectives: []
------------------------------
noun: energiatootmine 
top 5 adjectives: []
------------------------------
noun: lillesibul 
top 5 adjectives: []
------------------------------
noun: tuulekiirus 
top 5 adjectives: []
------------------------------
noun: montaaž 
top 5 adjectives: []
------------------------------
noun: tööstaazh 
top 5 adjectives: []
------------------------------
noun: liidripositsioon 
top 5 adjectives: []
------------------------------
noun: Interneti-ühendus 
top 5 adjectives: []
------------------------------
noun: t

noun: inimkaubandus 
top 5 adjectives: []
------------------------------
noun: jalgpallielu 
top 5 adjectives: []
------------------------------
noun: väänik 
top 5 adjectives: []
------------------------------
noun: plomm 
top 5 adjectives: []
------------------------------
noun: tropp 
top 5 adjectives: []
------------------------------
noun: veiniäädikas 
top 5 adjectives: []
------------------------------
noun: kuludokument 
top 5 adjectives: []
------------------------------
noun: taskurätt 
top 5 adjectives: []
------------------------------
noun: gospel 
top 5 adjectives: []
------------------------------
noun: lähteandmed 
top 5 adjectives: []
------------------------------
noun: finants 
top 5 adjectives: []
------------------------------
noun: maksudeklaratsioon 
top 5 adjectives: []
------------------------------
noun: pommitamine 
top 5 adjectives: []
------------------------------
noun: ladustusleping 
top 5 adjectives: []
------------------------------
noun: aeglus 
top 5

In [210]:
for idx, row in data.iterrows():
    print("noun:", idx,"\ntop 5 adjectives:" , list(row.sort_values(ascending=False).head().index))
    print("------------------------------")

noun: aasta 
top 5 adjectives: ['eelmine', 'järgmine', 'viimane', 'tulev', 'käesolev']
------------------------------
noun: aeg 
top 5 adjectives: ['viimane', 'kogu', 'pikk', 'õige', 'vaba']
------------------------------
noun: määrus 
top 5 adjectives: ['käesolev', 'muudetud', 'kõnealune', 'käsitlev', 'uus']
------------------------------
noun: omavalitsus 
top 5 adjectives: ['kohalik', 'uus', 'väike', 'suur', 'piirkondlik']
------------------------------
noun: osa 
top 5 adjectives: ['suur', 'oluline', 'valdav', 'väike', 'lahutamatu']
------------------------------
noun: tänu 
top 5 adjectives: ['suur', 'eriline', 'siiras', 'võimalik', 'südamlik']
------------------------------
noun: nädal 
top 5 adjectives: ['eelmine', 'järgmine', 'viimane', 'läinud', 'tulev']
------------------------------
noun: isik 
top 5 adjectives: ['juriidiline', 'füüsiline', 'asjaomane', 'avalik-õiguslik', 'eraõiguslik']
------------------------------
noun: maailm 
top 5 adjectives: ['kogu', 'terve', 'vana', 

noun: hind 
top 5 adjectives: ['kõrge', 'keskmine', 'soodne', 'uus', 'madal']
------------------------------
noun: roll 
top 5 adjectives: ['oluline', 'suur', 'tähtis', 'uus', 'keskne']
------------------------------
noun: süsteem 
top 5 adjectives: ['uus', 'kogu', 'praegune', 'poliitiline', 'ühtne']
------------------------------
noun: nimi 
top 5 adjectives: ['uus', 'õige', 'hea', 'ilus', 'ametlik']
------------------------------
noun: koostöö 
top 5 adjectives: ['tihe', 'rahvusvaheline', 'hea', 'vaheline', 'omavaheline']
------------------------------
noun: eeskiri 
top 5 adjectives: ['üksikasjalik', 'uus', 'käsitlev', 'ühine', 'tehniline']
------------------------------
noun: vesi 
top 5 adjectives: ['soe', 'külm', 'puhas', 'kuum', 'keev']
------------------------------
noun: seisund 
top 5 adjectives: ['tervislik', 'raske', 'monopoolne', 'õiguslik', 'hea']
------------------------------
noun: aine 
top 5 adjectives: ['narkootiline', 'psühhotroopne', 'ohtlik', 'orgaaniline', 'keemi

noun: tööstus 
top 5 adjectives: ['töötlev', 'kohalik', 'kodumaine', 'kogu', 'suur']
------------------------------
noun: muusika 
top 5 adjectives: ['klassikaline', 'hea', 'uus', 'elav', 'elektrooniline']
------------------------------
noun: hinnang 
top 5 adjectives: ['esialgne', 'erinev', 'positiivne', 'negatiivne', 'õiguslik']
------------------------------
noun: kohtlemine 
top 5 adjectives: ['võrdne', 'ebavõrdne', 'halb', 'julm', 'ebainimlik']
------------------------------
noun: külg 
top 5 adjectives: ['hea', 'tugev', 'nõrk', 'positiivne', 'halb']
------------------------------
noun: revolutsioon 
top 5 adjectives: ['laulev', 'oranž', 'uus', 'suur', 'värviline']
------------------------------
noun: kuju 
top 5 adjectives: ['praegune', 'muudetud', 'endine', 'muutmata', 'puhas']
------------------------------
noun: hoog 
top 5 adjectives: ['täis', 'uus', 'hea', 'suur', 'õige']
------------------------------
noun: alkohol 
top 5 adjectives: ['kange', 'lahja', 'alaealine', 'illegaa

noun: karistus 
top 5 adjectives: ['rahaline', 'karm', 'võimalik', 'õiglane', 'vabaduskaotuslik']
------------------------------
noun: võit 
top 5 adjectives: ['suur', 'kindel', 'järjestikune', 'ülekaalukas', 'eilne']
------------------------------
noun: kava 
top 5 adjectives: ['esialgne', 'praegune', 'uus', 'kõnealune', 'kindel']
------------------------------
noun: meeskond 
top 5 adjectives: ['kogu', 'uus', 'tugev', 'hea', 'noor']
------------------------------
noun: korrus 
top 5 adjectives: ['ülemine', 'alumine', 'viimane', 'uus', 'terve']
------------------------------
noun: nägu 
top 5 adjectives: ['uus', 'tõsine', 'hea', 'tuttav', 'rõõmus']
------------------------------
noun: kultuur 
top 5 adjectives: ['poliitiline', 'erinev', 'eri', 'uus', 'kohalik']
------------------------------
noun: tellimus 
top 5 adjectives: ['riiklik', 'poliitiline', 'sotsiaalne', 'uus', 'suur']
------------------------------
noun: olümpiakomitee 
top 5 adjectives: ['rahvusvaheline', 'rahvuslik', 'ko

noun: keha 
top 5 adjectives: ['kogu', 'terve', 'füüsiline', 'paljas', 'ilus']
------------------------------
noun: lause 
top 5 adjectives: ['viimane', 'järgmine', 'öeldud', 'eelmine', 'pikk']
------------------------------
noun: säte 
top 5 adjectives: ['käsitlev', 'vastav', 'kõnealune', 'asjakohane', 'reguleeriv']
------------------------------
noun: kaitse 
top 5 adjectives: ['sotsiaalne', 'riiklik', 'hea', 'tugev', 'kollektiivne']
------------------------------
noun: laev 
top 5 adjectives: ['uus', 'sõitev', 'suur', 'valge', 'kuuluv']
------------------------------
noun: kuupalk 
top 5 adjectives: ['keskmine', '000kroonine', 'suurune', 'kindel', 'kroonine']
------------------------------
noun: surve 
top 5 adjectives: ['tugev', 'poliitiline', 'rahvusvaheline', 'suur', 'pidev']
------------------------------
noun: vaev 
top 5 adjectives: ['suur', 'kerge', 'vähene', 'ränk', 'eriline']
------------------------------
noun: identiteet 
top 5 adjectives: ['rahvuslik', 'uus', 'kultuurili

...

noun: lüke 
top 5 adjectives: ['kaval', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: kriminaalkaristus 
top 5 adjectives: ['kehtiv', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: olmetingimus 
top 5 adjectives: ['kehv', 'raudteeäärne', '47aastane', '48aastane', '6000kroonine']
------------------------------
noun: pelmeen 
top 5 adjectives: ['keedetud', 'raudteeäärne', 'lepingueelne', '48aastane', '6000kroonine']
------------------------------
noun: keik 
top 5 adjectives: ['kena', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------------------------------
noun: põletus 
top 5 adjectives: ['kerge', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------------------------------
noun: miinimummäär 
top 5 adjectives: ['kehtiv', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: topelttoll 
top 5 adjectives: ['kehtiv', 'raudteeäärne', 'lastud', '4

noun: taimekasvatustava 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: võistlejanärv 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: nuss 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: lektor 
top 5 adjectives: ['olnud', 'hea', 'raudteeäärne', 'lenduv', '48aastane']
------------------------------
noun: treeningupartner 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: mänedzher 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: laulusõna 
top 5 adjectives: ['hea', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: aksessuaar 
top 5 adjectives: ['kõikvõimalik', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------

noun: põllumajandustulu 
top 5 adjectives: ['kindel', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: netomüügihind 
top 5 adjectives: ['keskmine', 'raudteeäärne', '1toaline', '2aastane', '47aastane']
------------------------------
noun: jahtumine 
top 5 adjectives: ['kiire', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: võidumõte 
top 5 adjectives: ['kindel', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: rikastumisvõimalus 
top 5 adjectives: ['kiire', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: idanemine 
top 5 adjectives: ['kiire', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: nullimäng 
top 5 adjectives: ['järjestikune', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: konkurentsivabadus 
top 5 adjectives: ['järgmine', 'raudteeäärne', '

noun: täideviija 
top 5 adjectives: ['otsene', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: angažeeritus 
top 5 adjectives: ['poliitiline', 'lastud', '2aastane', '47aastane', '48aastane']
------------------------------
noun: otsustamatus 
top 5 adjectives: ['poliitiline', 'lastud', '2aastane', '47aastane', '48aastane']
------------------------------
noun: mahhinatsioon 
top 5 adjectives: ['poliitiline', 'lastud', '2aastane', '47aastane', '48aastane']
------------------------------
noun: agenda 
top 5 adjectives: ['poliitiline', 'lastud', '2aastane', '47aastane', '48aastane']
------------------------------
noun: nakkusallikas 
top 5 adjectives: ['potentsiaalne', 'raudteeäärne', '1toaline', '2aastane', '47aastane']
------------------------------
noun: menetlusnorm 
top 5 adjectives: ['oluline', 'lastud', '2aastane', '47aastane', '48aastane']
------------------------------
noun: alusdokument 
top 5 adjectives: ['oluline', 'lastud', '2aastane', '

------------------------------
noun: gospel 
top 5 adjectives: ['valge', 'raudteeäärne', '1toaline', '2aastane', '47aastane']
------------------------------
noun: lähteandmed 
top 5 adjectives: ['vajalik', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------------------------------
noun: finants 
top 5 adjectives: ['vajalik', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------------------------------
noun: maksudeklaratsioon 
top 5 adjectives: ['perioodiline', 'raudteeäärne', 'lastud', '2aastane', '47aastane']
------------------------------
noun: pommitamine 
top 5 adjectives: ['pidev', 'lenduv', '48aastane', '6000kroonine', 'lahtiklopitud']
------------------------------
noun: ladustusleping 
top 5 adjectives: ['pikaajaline', 'raudteeäärne', 'lepingueelne', '47aastane', '48aastane']
------------------------------
noun: aeglus 
top 5 adjectives: ['piinav', 'raudteeäärne', 'lastud', '47aastane', '48aastane']
------------------------------
noun: sotsiaalkindlustu

In [211]:
len(diff_pairs['aasta'])

54

In [213]:
len(data.loc['aasta'][data.loc['aasta'] > 0])

257

In [220]:
data['punane'][data['punane'] > 0].sort_values(ascending=False).head(10)

vein      1105
rist      1054
kaart      973
tuli       814
värv       631
latern     525
väljak     497
joon       349
lipp       339
vaip       294
Name: punane, dtype: int64

In [221]:
punased = []
for key, val in diff_pairs.items():
    if 'punane' in val:
        punased.append(key)

In [222]:
print(punased)

['pea', 'kiri', 'tänav', 'raamat', 'nägu', 'täht', 'liha', 'pipar', 'puu', 'nina', 'püks', 'grupp', 'joon', 'katus', 'särk', 'pass', 'kala', 'laik', 'minevik', 'riie', 'valgus', 'vilkur', 'sibul', 'mantel', 'triip', 'kalamari', 'kaas', 'terror', 'nupp', 'lint', 'nelk', 'kukk', 'tõug', 'täpp', 'müts', 'mari', 'päevakübar', 'tuluke', 'kärbseseen', 'khmeer', 'lauavein', 'niit', 'värvus', 'lips', 'viisnurk', 'rätt']


In [223]:
len(data['punane'][data['punane'] > 0])

268

In [224]:
len(punased)

46

### NMF on diff data

In [70]:
with open("nmf_model_diff.pickle", "rb") as f:
    nmf_diff = pickle.load(f)

C:\Users\Birgit\Anaconda3\envs\py36_estnltk\lib\site-packages\sklearn\base.py:334: UserWarning: Trying to unpickle estimator NMF from version 0.22.2.post1 when using version 0.23.2. This might lead to breaking code or invalid results. Use at your own risk.
  UserWarning)


In [73]:
results_diff = np.load("nmf_model_results_diff.npy")

In [74]:
diff_adjs_in_topics = pd.DataFrame(nmf_diff.components_, columns=diff_df.columns)
diff_nouns_in_topics = pd.DataFrame(results_diff, index=diff_df.index)

In [75]:
diff_adjs_in_topics.head()

eelmine  järgmine   viimane   käesolev      kogu    kohalik       suur  \
0  0.000000  0.004216  0.385959  66.660466  7.402061   0.000000   1.359169   
1  0.000000  0.000000  0.000000   0.000000  0.000000   0.000000  84.892507   
2  0.042432  0.017341  0.003904   2.595364  2.958597  21.217993   2.177572   
3  0.000000  0.000000  0.000000   0.000000  0.000000   0.000000   0.000000   
4  0.000000  0.000000  0.000000   0.000000  0.000000   0.000000   0.000000   

       pikk  juriidiline     tulev  ...  realiseeritav  valgustatav  vajuv  \
0  4.839502          0.0  0.024106  ...            0.0          0.0    0.0   
1  0.000000          0.0  0.000000  ...            0.0          0.0    0.0   
2  0.088834          0.0  0.140868  ...            0.0          0.0    0.0   
3  0.000000          0.0  0.000000  ...            0.0          0.0    0.0   
4  0.000000          0.0  0.000000  ...            0.0          0.0    0.0   

   väikesekasvuline  väikeseformaadiline  õlirikas  õigusetu  oletuslik  \
0               0.0                  0.0       0.0       0.0        0.0   
1               0.0                  0.0       0.0       0.0        0.0   
2               0.0                  0.0       0.0       0.0        0.0   
3               0.0                  0.0       0.0       0.0        0.0   
4               0.0                  0.0       0.0       0.0        0.0   

   raugematu  raudteeäärne  
0        0.0           0.0  
1        0.0           0.0  
2        0.0           0.0  
3        0.0           0.0  
4        0.0           0.0  

[5 rows x 7358 columns]

In [76]:
diff_nouns_in_topics.head()

0         1          2         3         4         5    \
aasta        59.341629  0.067943   0.000000  1.062085  0.399896  6.164183   
aeg           0.000000  0.537416  56.319229  0.000000  8.092288  1.803880   
määrus        0.000000  0.000000   0.000000  0.145941  0.000000  0.007589   
omavalitsus   0.000000  0.970097   0.000000  0.000000  1.593559  0.094279   
osa           0.000000  0.072112   0.000000  0.072484  0.001552  0.463092   

             6    7         8          9    ...  990  991       992  993  \
aasta        0.0  0.0  7.792796   1.316098  ...  0.0  0.0  0.000000  0.0   
aeg          0.0  0.0  6.310497  15.183030  ...  0.0  0.0  0.001230  0.0   
määrus       0.0  0.0  0.364059   0.000000  ...  0.0  0.0  0.000000  0.0   
omavalitsus  0.0  0.0  0.353129   0.000000  ...  0.0  0.0  0.008763  0.0   
osa          0.0  0.0  0.147304   0.065435  ...  0.0  0.0  0.000000  0.0   

                  994  995  996  997  998  999  
aasta        0.005570  0.0  0.0  0.0  0.0  0.0  
aeg          0.003421  0.0  0.0  0.0  0.0  0.0  
määrus       0.000000  0.0  0.0  0.0  0.0  0.0  
omavalitsus  0.000000  0.0  0.0  0.0  0.0  0.0  
osa          0.001311  0.0  0.0  0.0  0.0  0.0  

[5 rows x 1000 columns]

In [77]:
topics_diff = defaultdict(list)

for i, row in diff_nouns_in_topics.iterrows():
    topics_diff[row.idxmax()].append(i)

In [80]:
colours = ['valge', 'kollane', 'oranž', 'roosa', 'punane', 'pruun', 'roheline', 'sinine', 'lilla', 'hall', 'must']

In [93]:
colours_topics_diff = defaultdict(list)

for colour in colours:
    col_topics = diff_adjs_in_topics[colour].sort_values(ascending=False).head(3)
    for index in col_topics.index:
        colours_topics_diff[index].append(colour)

In [94]:
colours_topics_diff

defaultdict(list,
            {395: ['valge', 'punane', 'sinine', 'hall', 'must'],
             140: ['valge', 'roheline'],
             104: ['valge'],
             729: ['kollane', 'oranž', 'lilla'],
             146: ['kollane'],
             429: ['kollane', 'roheline', 'must'],
             713: ['oranž', 'roosa'],
             428: ['oranž'],
             941: ['roosa', 'lilla'],
             463: ['roosa'],
             795: ['punane', 'pruun'],
             617: ['punane'],
             832: ['pruun', 'sinine'],
             482: ['pruun'],
             460: ['roheline'],
             332: ['sinine'],
             518: ['lilla'],
             484: ['hall'],
             658: ['hall'],
             348: ['must']})

In [98]:
diff_nouns_in_topics[395].sort_values(ascending=False).head(10)

pilt          0.006282
kujutis       0.000076
vaatepilt     0.000065
joonis        0.000031
graafika      0.000030
video         0.000030
sõim          0.000028
foto          0.000027
laul          0.000023
karikatuur    0.000021
Name: 395, dtype: float64

In [100]:
days = ['esmaspäev', 'teisipäev', 'kolmapäev', 'neljapäev', 'reede', 'laupäev', 'pühapäev']
idx2_diff = []

for day in days:
    for topic, words in topics_diff.items():
        if day in words:
            idx2_diff.append(topic)
            continue

In [101]:
idx2_diff

[297, 406, 406, 406, 347, 113, 314]

In [102]:
for i in set(idx2_diff):
    print(i, ":", topics_diff[i])
    print("Most common adjectives in topic:")
    print(diff_adjs_in_topics.loc[i].sort_values(ascending=False).head())
    print("----------------------------")

297 : ['aasta', 'aeg', 'osa', 'maailm', 'kolleeg', 'seadus', 'palk', 'inimene', 'mees', 'valitsus', 'valimine', 'maja', 'leping', 'hooaeg', 'naine', 'elanik', 'töökoht', 'olukord', 'juht', 'laps', 'elu', 'otsus', 'minister', 'probleem', 'sõda', 'liige', 'riik', 'hoone', 'liikmesriik', 'meede', 'raha', 'sõna', 'riigikogu', 'põlvkond', 'asi', 'töö', 'areng', 'mäng', 'suvi', 'hind', 'roll', 'süsteem', 'nimi', 'koostöö', 'plaat', 'konkurss', 'nõukogu', 'kodu', 'sajand', 'mudel', 'juhatus', 'film', 'muutus', 'tee', 'korter', 'nõue', 'kohustus', 'peaminister', 'esimees', 'plaan', 'investor', 'investeering', 'kuju', 'raamat', 'linn', 'riigiametnik', 'tulu', 'oht', 'muudatus', 'sügis', 'programm', 'album', 'projekt', 'edu', 'õigusakt', 'koosseis', 'koalitsioon', 'meeskond', 'volikogu', 'täht', 'julgeolek', 'tehas', 'ülikool', 'operatsioon', 'eelarve', 'näitleja', 'ettevõte', 'ülesanne', 'poliitika', 'saatus', 'kulu', 'peatreener', 'kunstnik', 'kodanik', 'õpetaja', 'maailmameister', 'linnapea',